## Load dataset and tree info

In [1]:
from sklearn.datasets import load_iris
import pandas as pd
from sklearn.preprocessing import StandardScaler
import numpy as np
from keras.layers import Dense, Input, concatenate, GRU, LSTM
from keras import backend as K
from keras.utils import to_categorical
from keras import Model
from nltk.translate.bleu_score import sentence_bleu

Using TensorFlow backend.


In [2]:
iris = load_iris()
X = iris['data']
y = iris['target']
scaler = StandardScaler()
scaler.fit(X)
X = scaler.transform(X)

In [3]:
df = pd.DataFrame(X)

In [4]:
bin_labels = pd.read_csv('../../data/raw/local_dt/local_iris_bin_labels.csv', delimiter=",")

In [5]:
bin_labels = bin_labels.rename(columns={"Unnamed: 0": "label", "label_list": "bins"})

In [6]:
bin_labels

label     x
0       A  0.65
1       B  1.60
2       C  2.70
3       D  2.95
4       E  4.65
5       F  5.15
6       G  5.80
7       H  0.75
8       I  1.65
9       J  3.05
10      K  5.45
11      L  6.15
12      M  1.00
13      N  2.85
14      O  3.25
15      P  5.55
16      Q  0.60
17      R  1.85
18      S  2.90
19      T  3.10
20      U  5.05
21      V  5.35
22      W  0.80
23      X  1.45
24      Y  3.20
25      Z  4.75
26     AB  5.95
27     AC  0.70
28     AD  2.50
29     AE  3.35
..    ...   ...
90     CS  5.60
91     CT  4.35
92     CU  1.70
93     CV  0.95
94     CW  4.30
95     CX  5.75
96     CY  2.35
97     CZ  5.00
98     DE  6.35
99     DF  1.35
100    DG  7.30
101    DH  6.40
102    DI  6.70
103    DJ  3.85
104    DK  6.60
105    DL  7.20
106    DM  7.35
107    DN  6.85
108    DO  1.40
109    DP  7.00
110    DQ  0.55
111    DR  4.40
112    DS  2.25
113    DT  2.20
114    DU  1.30
115    DV  6.95
116    DW  4.15
117    DX  1.10
118    DY  1.15
119    DZ  1.25

[120 rows x 2 columns]

In [7]:
# path_df = pd.read_csv('../../data/raw/rpart_paths.csv', delimiter=",")
# path_df = pd.read_csv('../../data/raw/test_paths.csv', delimiter=",")
path_df = pd.read_csv('../../data/raw/local_dt/local_iris_paths.csv', delimiter=",")

In [8]:
path_df = path_df.drop(["Unnamed: 0"], axis=1)
path_df = path_df.rename(columns={list(path_df)[0]: "new_col"})

In [9]:
test_data = pd.concat([df, path_df], axis=1)
# test_data = df

In [10]:
test_data

0         1         2         3    new_col
0   -0.900681  1.019004 -1.340227 -1.315444    1G0,2D1
1   -1.143017 -0.131979 -1.340227 -1.315444    3E0,1K0
2   -1.385353  0.328414 -1.397064 -1.315444        1P0
3   -1.506521  0.098217 -1.283389 -1.315444        3C0
4   -1.021849  1.249201 -1.340227 -1.315444    3Z0,1K0
5   -0.537178  1.939791 -1.169714 -1.052180       2AE1
6   -1.506521  0.788808 -1.340227 -1.183812        2J1
7   -1.021849  0.788808 -1.283389 -1.315444       3AL0
8   -1.748856 -0.362176 -1.340227 -1.315444        3C0
9   -1.143017  0.098217 -1.283389 -1.447076       1AG0
10  -0.537178  1.479398 -1.283389 -1.315444       1AF0
11  -1.264185  0.788808 -1.226552 -1.315444        2T1
12  -1.264185 -0.131979 -1.340227 -1.447076       3AY0
13  -1.870024 -0.131979 -1.510739 -1.447076       3AD0
14  -0.052506  2.169988 -1.453901 -1.315444  3BH0,2AS1
15  -0.173674  3.090775 -1.283389 -1.052180  3AI0,2AS1
16  -0.537178  1.939791 -1.397064 -1.052180       1AF0
17  -0.900681  1.019004 -1.340227 -1.183812   2D1,1AG0
18  -0.173674  1.709595 -1.169714 -1.183812  4AW0,2BQ1
19  -0.900681  1.709595 -1.283389 -1.183812       1BF0
20  -0.537178  0.788808 -1.169714 -1.315444   1AB0,1K0
21  -0.900681  1.479398 -1.283389 -1.052180       3AD0
22  -1.506521  1.249201 -1.567576 -1.315444       3AY0
23  -0.900681  0.558611 -1.169714 -0.920548   3BX0,1V0
24  -1.264185  0.788808 -1.056039 -1.315444       3BU0
25  -1.021849 -0.131979 -1.226552 -1.315444        3N0
26  -1.021849  0.788808 -1.226552 -1.052180  1CF0,1AF0
27  -0.779513  1.019004 -1.283389 -1.315444        3T0
28  -0.779513  0.788808 -1.340227 -1.315444       3AD0
29  -1.385353  0.328414 -1.226552 -1.315444  2BK1,1BI0
..        ...       ...       ...       ...        ...
120  1.280340  0.328414  1.103783  1.448832       3AJ1
121 -0.294842 -0.592373  0.649083  1.053935       3DR1
122  2.249683 -0.592373  1.672157  1.053935        1G1
123  0.553333 -0.822570  0.649083  0.790671  3BZ1,1BL1
124  1.038005  0.558611  1.103783  1.185567       3BH1
125  1.643844  0.328414  1.274295  0.790671       1CX1
126  0.432165 -0.592373  0.592246  0.790671   3S1,1AG1
127  0.310998 -0.131979  0.649083  0.790671       3BM1
128  0.674501 -0.592373  1.046945  1.185567       1AN1
129  1.643844 -0.131979  1.160620  0.527406       1AB1
130  1.886180 -0.592373  1.331133  0.922303        3Z1
131  2.492019  1.709595  1.501645  1.053935       3AI1
132  0.674501 -0.592373  1.046945  1.317199    1V1,3U1
133  0.553333 -0.592373  0.762758  0.395774       1BL1
134  0.310998 -1.052767  1.046945  0.264142       1AF1
135  2.249683 -0.131979  1.331133  1.448832       3CZ1
136  0.553333  0.788808  1.046945  1.580464       3CN1
137  0.674501  0.098217  0.990108  0.790671       3AI1
138  0.189830 -0.131979  0.592246  0.790671       3CQ1
139  1.280340  0.098217  0.933271  1.185567       3AP1
140  1.038005  0.098217  1.046945  1.580464  1CX1,3AP1
141  1.280340  0.098217  0.762758  1.448832  1CP1,3CN1
142 -0.052506 -0.822570  0.762758  0.922303       1CX1
143  1.159173  0.328414  1.217458  1.448832        1K1
144  1.038005  0.558611  1.103783  1.712096  1CX1,3AI1
145  1.038005 -0.131979  0.819596  1.448832       3AP1
146  0.553333 -1.282963  0.705921  0.922303       3AJ1
147  0.795669 -0.131979  0.819596  1.053935       1BI1
148  0.432165  0.788808  0.933271  1.448832   2S1,1CR1
149  0.068662 -0.131979  0.762758  0.790671       3AI1

[150 rows x 5 columns]

### Transform path df

In [11]:
new_path = []
for i, val in test_data.iterrows():
    new_path.append(val['new_col'].split(sep=","))

In [12]:
test_data.head()

0         1         2         3 new_col
0 -0.900681  1.019004 -1.340227 -1.315444     1G0
1 -1.143017 -0.131979 -1.340227 -1.315444     3J0
2 -1.385353  0.328414 -1.397064 -1.315444     1U0
3 -1.506521  0.098217 -1.283389 -1.315444    1AC0
4 -1.021849  1.249201 -1.340227 -1.315444     1N0

In [13]:
[x.insert(0, 'S') for x in new_path]
[x.append('E') for x in new_path]

[None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,

In [14]:
new_path

[['S', '1G0', 'E'],
 ['S', '3J0', 'E'],
 ['S', '1U0', 'E'],
 ['S', '1AC0', 'E'],
 ['S', '1N0', 'E'],
 ['S', '1AO0', 'E'],
 ['S', '2Y1', 'E'],
 ['S', '1G0', 'E'],
 ['S', '3AK0', 'E'],
 ['S', '1V0', 'E'],
 ['S', '3R0', 'E'],
 ['S', '3J0', 'E'],
 ['S', '3R0', 'E'],
 ['S', '3BJ0', 'E'],
 ['S', '3Y0', 'E'],
 ['S', '3X0', 'E'],
 ['S', '1V0', 'E'],
 ['S', '3F0', '1BM0', 'E'],
 ['S', '1BU0', '3BR0', 'E'],
 ['S', '3F0', '1G0', 'E'],
 ['S', '1O0', 'E'],
 ['S', '3BJ0', 'E'],
 ['S', '1V0', '1AH0', 'E'],
 ['S', '1O0', 'E'],
 ['S', '3F0', '1AO0', 'E'],
 ['S', '3U0', '1AO0', 'E'],
 ['S', '3AK0', 'E'],
 ['S', '1AC0', 'E'],
 ['S', '3F0', '1G0', 'E'],
 ['S', '2E1', 'E'],
 ['S', '3BL0', '2AM1', 'E'],
 ['S', '3D0', 'E'],
 ['S', '3M0', '1G0', 'E'],
 ['S', '3F0', '2CN1', 'E'],
 ['S', '1M0', 'E'],
 ['S', '1BM0', 'E'],
 ['S', '3X0', 'E'],
 ['S', '3AS0', 'E'],
 ['S', '3AN0', '1BL0', 'E'],
 ['S', '3Y0', 'E'],
 ['S', '1CE0', 'E'],
 ['S', '1BF0', 'E'],
 ['S', '2E1', 'E'],
 ['S', '3X0', 'E'],
 ['S', '3BJ0', 'E'],


In [15]:
test_data['new_path'] = new_path

In [2]:
# 3G1', '4E0', '3R0', '4D0
# 3G1', '4E1', '3Q1
# a = [1,0,0,0]
# b = [1,1,1]
# c = [0]

In [16]:
test_data = test_data.drop(["new_col"], axis=1)

In [17]:
test_data.head()

0         1         2         3      new_path
0 -0.900681  1.019004 -1.340227 -1.315444   [S, 1G0, E]
1 -1.143017 -0.131979 -1.340227 -1.315444   [S, 3J0, E]
2 -1.385353  0.328414 -1.397064 -1.315444   [S, 1U0, E]
3 -1.506521  0.098217 -1.283389 -1.315444  [S, 1AC0, E]
4 -1.021849  1.249201 -1.340227 -1.315444   [S, 1N0, E]

In [18]:
paths_lengths = np.array([len(xi)
                          for xi in test_data.iloc[:,-1]])

In [19]:
paths_lengths
np.max(paths_lengths)

5

In [20]:
label_char = []
for _, i in enumerate(np.unique(test_data['new_path'])):
    for _, j in enumerate(i):
        if j not in label_char:
            label_char.append(j)

In [21]:
label_indices = { j : i for i, j in enumerate(label_char) }

In [22]:
label_indices

{'S': 0,
 '1AC0': 1,
 'E': 2,
 '1AC1': 3,
 '1AZ0': 4,
 '1BN1': 5,
 '3AY1': 6,
 '3BT0': 7,
 '1AD0': 8,
 '3R0': 9,
 '1AO0': 10,
 '1AO1': 11,
 '1BW0': 12,
 '1DG0': 13,
 '2J0': 14,
 '1P1': 15,
 '3CX1': 16,
 '3U1': 17,
 '1AP0': 18,
 '1CH1': 19,
 '1AZ1': 20,
 '1AV1': 21,
 '1BF0': 22,
 '1BM0': 23,
 '1BN0': 24,
 '1BX1': 25,
 '1BU0': 26,
 '3BR0': 27,
 '1BU1': 28,
 '1CE0': 29,
 '1CE1': 30,
 '1CL0': 31,
 '3AH1': 32,
 '3CX0': 33,
 '1CX1': 34,
 '1DI1': 35,
 '1G0': 36,
 '1G1': 37,
 '2AM0': 38,
 '3BL0': 39,
 '1H1': 40,
 '1M0': 41,
 '1N0': 42,
 '1N1': 43,
 '1AV0': 44,
 '1O0': 45,
 '1O1': 46,
 '1DI0': 47,
 '2AM1': 48,
 '3AH0': 49,
 '3CF0': 50,
 '3CH0': 51,
 '1U0': 52,
 '1V0': 53,
 '1AH0': 54,
 '1V1': 55,
 '3CI0': 56,
 '3F1': 57,
 '2AG0': 58,
 '3T1': 59,
 '1DS1': 60,
 '2AT0': 61,
 '1CW0': 62,
 '3T0': 63,
 '4AQ1': 64,
 '2BD0': 65,
 '1CY0': 66,
 '1DF0': 67,
 '2E0': 68,
 '2E1': 69,
 '2L0': 70,
 '1DM1': 71,
 '2X0': 72,
 '2Y1': 73,
 '1BF1': 74,
 '3AB0': 75,
 '3AK0': 76,
 '3AK1': 77,
 '1DM0': 78,
 '3AL1': 79,

In [ ]:
### Move to bottom trials

test_data = pd.concat([test_data, path_df.loc[:,'updated_path']], axis=1)
updated_path = []
for i, val in test_data.iterrows():
    updated_path.append(val['updated_path'].split(sep=","))

_ = [x.insert(0, 'S') for x in updated_path]
_ = [x.append('E') for x in updated_path]

test_data['updated_path'] = updated_path

# test_data = test_data.drop(["updated_path"], axis=1)

paths_lengths = np.array([len(xi) for xi in test_data.iloc[:,-1]])

label_char = []
for _, i in enumerate(np.unique(test_data['updated_path'])):
    for _, j in enumerate(i):
        if j not in label_char:
            label_char.append(j)

label_indices = { j : i for i, j in enumerate(label_char) }
indices_label = { i : j for i, j in enumerate(label_char) }

input_path_sequence = []
next_chars = []
features = []
paths_maxlen = np.max(paths_lengths)
# path_vocab_size = len(bin_labels) # How is this working? Validate!
path_vocab_size = len(indices_label) # Temporary test for local trees
feature_size = 4
for i in range(0, len(test_data)):
    # get the feature
    curr_feat = np.array([test_data.iloc[i, 0:4]])
    curr_path = test_data.iloc[i, -1]
    curr_path_len = len(curr_path)
    # curr_label = y[i]
    # curr_dec_feat = df.iloc[i, 6]
    for j in range(1, curr_path_len):
        features.append(curr_feat)
        input_path_sequence.append(curr_path[0:j])
        next_chars.append(curr_path[j])

## Vectorize inputs        

x_path = np.zeros(
    (len(input_path_sequence), paths_maxlen, path_vocab_size), dtype=np.bool)

path_latent_input = np.zeros(
    (len(input_path_sequence), feature_size), dtype=np.float)

y_path = np.zeros(
    (len(input_path_sequence), path_vocab_size), dtype=np.bool)

# print(input_path_sequence)
# print(len(input_path_sequence))
for i, sentence in enumerate(input_path_sequence):
    for t, char in enumerate(sentence):
        # x_path[i, t, self.char_indices[char]] = 1
        # print(bin_labels.index[bin_labels['label'] == char[1]])
        # index = bin_labels.index[bin_labels['label'] == char[1]].tolist()[0]
        x_path[i, t, label_indices[char]] = 1
    # y_path[i, char_indices[next_chars[i]]] = 1
    # index = bin_labels.index[bin_labels['label'] == next_chars[i][1]].tolist()[0]
    # y_path[i, index] = 1
    y_path[i, label_indices[next_chars[i]]] = 1
    path_latent_input[i, :] = features[i]

In [220]:
test_data = test_data.drop(["updated_path"], axis=1)

In [23]:
len(label_indices)

117

In [24]:
indices_label = { i : j for i, j in enumerate(label_char) }
indices_label

{0: 'S',
 1: '1AC0',
 2: 'E',
 3: '1AC1',
 4: '1AZ0',
 5: '1BN1',
 6: '3AY1',
 7: '3BT0',
 8: '1AD0',
 9: '3R0',
 10: '1AO0',
 11: '1AO1',
 12: '1BW0',
 13: '1DG0',
 14: '2J0',
 15: '1P1',
 16: '3CX1',
 17: '3U1',
 18: '1AP0',
 19: '1CH1',
 20: '1AZ1',
 21: '1AV1',
 22: '1BF0',
 23: '1BM0',
 24: '1BN0',
 25: '1BX1',
 26: '1BU0',
 27: '3BR0',
 28: '1BU1',
 29: '1CE0',
 30: '1CE1',
 31: '1CL0',
 32: '3AH1',
 33: '3CX0',
 34: '1CX1',
 35: '1DI1',
 36: '1G0',
 37: '1G1',
 38: '2AM0',
 39: '3BL0',
 40: '1H1',
 41: '1M0',
 42: '1N0',
 43: '1N1',
 44: '1AV0',
 45: '1O0',
 46: '1O1',
 47: '1DI0',
 48: '2AM1',
 49: '3AH0',
 50: '3CF0',
 51: '3CH0',
 52: '1U0',
 53: '1V0',
 54: '1AH0',
 55: '1V1',
 56: '3CI0',
 57: '3F1',
 58: '2AG0',
 59: '3T1',
 60: '1DS1',
 61: '2AT0',
 62: '1CW0',
 63: '3T0',
 64: '4AQ1',
 65: '2BD0',
 66: '1CY0',
 67: '1DF0',
 68: '2E0',
 69: '2E1',
 70: '2L0',
 71: '1DM1',
 72: '2X0',
 73: '2Y1',
 74: '1BF1',
 75: '3AB0',
 76: '3AK0',
 77: '3AK1',
 78: '1DM0',
 79: '3AL1',

In [25]:
bin_labels

label  bins
0      A  0.80
1      B  1.35
2      C  1.55
3      D  1.65
4      E  1.75
5      F  1.85
6      G  2.45
7      H  2.55
8      I  2.65
9      J  2.85
10     K  2.95
11     L  3.10
12     M  3.15
13     N  3.35
14     O  4.45
15     P  4.75
16     Q  4.85
17     R  4.95
18     S  5.35
19     T  5.45
20     U  5.45
21     V  5.95
22     W  6.15
23     X  6.50
24     Y  6.95
25     Z  7.10

In [27]:
path_df

new_col
0               1G0
1               3J0
2               1U0
3              1AC0
4               1N0
5              1AO0
6               2Y1
7               1G0
8              3AK0
9               1V0
10              3R0
11              3J0
12              3R0
13             3BJ0
14              3Y0
15              3X0
16              1V0
17         3F0,1BM0
18        1BU0,3BR0
19          3F0,1G0
20              1O0
21             3BJ0
22         1V0,1AH0
23              1O0
24         3F0,1AO0
25         3U0,1AO0
26             3AK0
27             1AC0
28          3F0,1G0
29              2E1
..              ...
120             3U1
121         3Y1,3U1
122        2L0,1DM1
123        1AO1,1P1
124            3CX1
125             3F1
126  2AT0,4AQ1,1AD0
127        2Y1,1BF1
128       2AM0,1DS1
129            4AF1
130            4AF1
131            1DI1
132       3BR1,1AV1
133             3T1
134       1CE1,3AH1
135            4BG1
136        1N1,1AV1
137        2AG0,3T1
138         3S1,3T1
139             1P1
140            4AQ1
141            4AQ1
142       1CE1,3CX1
143        1AO1,3U1
144        1AZ1,3U1
145            4BZ1
146       1AC1,3AY1
147            1AO1
148         1V1,3F1
149             3U1

[150 rows x 1 columns]

### Vectorize path sequences

In [1]:
input_path_sequence = []
next_chars = []
features = []
paths_maxlen = np.max(paths_lengths)
# path_vocab_size = len(bin_labels) # How is this working? Validate!
path_vocab_size = len(indices_label) # Temporary test for local trees
feature_size = 4
for i in range(0, len(test_data)):
    # get the feature
    curr_feat = np.array([test_data.iloc[i, 0:4]])
    curr_path = test_data.iloc[i, -1]
    curr_path_len = len(curr_path)
    # curr_label = y[i]
    # curr_dec_feat = df.iloc[i, 6]
    for j in range(1, curr_path_len):
        features.append(curr_feat)
        input_path_sequence.append(curr_path[0:j])
        next_chars.append(curr_path[j])

x_path = np.zeros(
    (len(input_path_sequence), paths_maxlen, path_vocab_size), dtype=np.bool)

path_latent_input = np.zeros(
    (len(input_path_sequence), feature_size), dtype=np.float)

y_path = np.zeros(
    (len(input_path_sequence), path_vocab_size), dtype=np.bool)

# print(input_path_sequence)
# print(len(input_path_sequence))
for i, sentence in enumerate(input_path_sequence):
    for t, char in enumerate(sentence):
        # x_path[i, t, self.char_indices[char]] = 1
        # print(bin_labels.index[bin_labels['label'] == char[1]])
        # index = bin_labels.index[bin_labels['label'] == char[1]].tolist()[0]
        x_path[i, t, label_indices[char]] = 1
    # y_path[i, char_indices[next_chars[i]]] = 1
    # index = bin_labels.index[bin_labels['label'] == next_chars[i][1]].tolist()[0]
    # y_path[i, index] = 1
    y_path[i, label_indices[next_chars[i]]] = 1
    path_latent_input[i, :] = features[i]
    
## Trouble with "S" and "E" index values.

NameError: name 'np' is not defined

In [29]:
len(input_path_sequence)

381

In [30]:
len(next_chars)

381

In [31]:
y_path.shape

(381, 117)

### Create and train label and rnn models

In [60]:
def _create_label_model(latent_dim=5):
    input_layer = Input(shape=(feature_size,), name='ip_x')
    hidden_layer_x1 = Dense(20, activation='tanh',
                            name='hidden_x1')(input_layer)
    hidden_layer_x2 = Dense(20, activation='tanh',
                            name='hidden_x2')(hidden_layer_x1)
    hidden_layer_x3 = Dense(latent_dim, activation='tanh',
                            name='hidden_x3')(hidden_layer_x2)
    output_layer = Dense(len(np.unique(y)), activation='softmax',
                         name='op_x')(hidden_layer_x3)
    model = Model(input_layer, output_layer)
    return model

def _create_combined_model(initialize=True, rnn_cell='gru', latent_dim=5):

    label_model_latent = Input(shape=(latent_dim,), name='label_ip')
    path_input = Input(shape=(
        paths_maxlen, path_vocab_size), name='dec_feat_ip')
    if rnn_cell == 'gru':
        RNN = GRU
    else:
        RNN = LSTM

    decoder = RNN(latent_dim, return_state=False,
                  return_sequences=False, name='gru_seq')
    if initialize:
        decoder_outputs = decoder(
            path_input, initial_state=label_model_latent)
    else:
        decoder_outputs = decoder(path_input)

    merge_layer = concatenate(
        [label_model_latent, decoder_outputs], name='cat')
    output_chars = Dense(path_vocab_size,
                         activation='softmax', name='op_sent')(merge_layer)
    model = Model(
        [label_model_latent, path_input], output_chars)
    return model

In [ ]:
from keras.layers.merge import 

In [33]:
combined_model = _create_combined_model()
label_model = _create_label_model()

Instructions for updating:
Colocations handled automatically by placer.


In [66]:
def get_hidden_x(x, model, layer_num=3):
    def get_hidden_x_inner(model, layer_num=layer_num):
        return K.function([model.layers[0].input], [model.layers[layer_num].output])
    return get_hidden_x_inner(model, layer_num=layer_num)([x])[0]

In [38]:
def fit_model():

    y_cat = to_categorical(y)

    label_model.compile(
        optimizer='adam', loss='categorical_crossentropy', metrics=['accuracy'])
    label_model.fit(
        X, y_cat, batch_size=30, epochs=150, verbose=0, shuffle=True, validation_split=0.2)

    x_latent = get_hidden_x(path_latent_input, model=label_model)

    combined_model.compile(
        optimizer='adam', loss='categorical_crossentropy', metrics=['accuracy'])
    combined_model.fit([x_latent, x_path], y_path,
                           batch_size=30, epochs=1000, verbose=1, shuffle=True)

In [39]:
fit_model()

Epoch 1/1000
381/381 [==============================] - 0s 1ms/step - loss: 2.5280 - acc: 0.4173
Epoch 2/1000
381/381 [==============================] - 0s 112us/step - loss: 2.5128 - acc: 0.4278
Epoch 3/1000
381/381 [==============================] - 0s 124us/step - loss: 2.5097 - acc: 0.4226
Epoch 4/1000
381/381 [==============================] - 0s 112us/step - loss: 2.5075 - acc: 0.4226
Epoch 5/1000
381/381 [==============================] - 0s 117us/step - loss: 2.5052 - acc: 0.4226
Epoch 6/1000
381/381 [==============================] - 0s 112us/step - loss: 2.5031 - acc: 0.4226
Epoch 7/1000
381/381 [==============================] - 0s 103us/step - loss: 2.5014 - acc: 0.4226
Epoch 8/1000
381/381 [==============================] - 0s 112us/step - loss: 2.4988 - acc: 0.4226
Epoch 9/1000
381/381 [==============================] - 0s 100us/step - loss: 2.4978 - acc: 0.4226
Epoch 10/1000
381/381 [==============================] - 0s 115us/step - loss: 2.4949 - acc: 0.4226
Epoch 11/10

381/381 [==============================] - 0s 116us/step - loss: 2.2430 - acc: 0.4488
Epoch 84/1000
381/381 [==============================] - 0s 117us/step - loss: 2.2408 - acc: 0.4436
Epoch 85/1000
381/381 [==============================] - 0s 101us/step - loss: 2.2401 - acc: 0.4488
Epoch 86/1000
381/381 [==============================] - 0s 109us/step - loss: 2.2407 - acc: 0.4488
Epoch 87/1000
381/381 [==============================] - 0s 108us/step - loss: 2.2371 - acc: 0.4462
Epoch 88/1000
381/381 [==============================] - 0s 114us/step - loss: 2.2350 - acc: 0.4488
Epoch 89/1000
381/381 [==============================] - 0s 115us/step - loss: 2.2352 - acc: 0.4488
Epoch 90/1000
381/381 [==============================] - 0s 123us/step - loss: 2.2328 - acc: 0.4462
Epoch 91/1000
381/381 [==============================] - 0s 107us/step - loss: 2.2333 - acc: 0.4462
Epoch 92/1000
381/381 [==============================] - 0s 125us/step - loss: 2.2313 - acc: 0.4436
Epoch 93/1000


381/381 [==============================] - 0s 97us/step - loss: 2.1037 - acc: 0.4593
Epoch 246/1000
381/381 [==============================] - 0s 109us/step - loss: 2.1032 - acc: 0.4567
Epoch 247/1000
381/381 [==============================] - 0s 91us/step - loss: 2.1010 - acc: 0.4541
Epoch 248/1000
381/381 [==============================] - 0s 97us/step - loss: 2.0992 - acc: 0.4567
Epoch 249/1000
381/381 [==============================] - 0s 104us/step - loss: 2.1005 - acc: 0.4514
Epoch 250/1000
381/381 [==============================] - 0s 101us/step - loss: 2.0999 - acc: 0.4514
Epoch 251/1000
381/381 [==============================] - 0s 101us/step - loss: 2.0978 - acc: 0.4567
Epoch 252/1000
381/381 [==============================] - 0s 114us/step - loss: 2.0976 - acc: 0.4514
Epoch 253/1000
381/381 [==============================] - 0s 96us/step - loss: 2.0966 - acc: 0.4541
Epoch 254/1000
381/381 [==============================] - 0s 103us/step - loss: 2.0960 - acc: 0.4541
Epoch 255

381/381 [==============================] - 0s 100us/step - loss: 2.0308 - acc: 0.4646
Epoch 408/1000
381/381 [==============================] - 0s 107us/step - loss: 2.0282 - acc: 0.4593
Epoch 409/1000
381/381 [==============================] - 0s 93us/step - loss: 2.0296 - acc: 0.4593
Epoch 410/1000
381/381 [==============================] - 0s 97us/step - loss: 2.0282 - acc: 0.4593
Epoch 411/1000
381/381 [==============================] - 0s 105us/step - loss: 2.0278 - acc: 0.4593
Epoch 412/1000
381/381 [==============================] - 0s 100us/step - loss: 2.0266 - acc: 0.4646
Epoch 413/1000
381/381 [==============================] - 0s 109us/step - loss: 2.0269 - acc: 0.4619
Epoch 414/1000
381/381 [==============================] - 0s 100us/step - loss: 2.0271 - acc: 0.4567
Epoch 415/1000
381/381 [==============================] - 0s 107us/step - loss: 2.0286 - acc: 0.4672
Epoch 416/1000
381/381 [==============================] - 0s 108us/step - loss: 2.0270 - acc: 0.4541
Epoch 4

381/381 [==============================] - 0s 116us/step - loss: 1.9785 - acc: 0.4646
Epoch 570/1000
381/381 [==============================] - 0s 100us/step - loss: 1.9811 - acc: 0.4698
Epoch 571/1000
381/381 [==============================] - 0s 100us/step - loss: 1.9806 - acc: 0.4646
Epoch 572/1000
381/381 [==============================] - 0s 106us/step - loss: 1.9776 - acc: 0.4698
Epoch 573/1000
381/381 [==============================] - 0s 104us/step - loss: 1.9823 - acc: 0.4541
Epoch 574/1000
381/381 [==============================] - 0s 98us/step - loss: 1.9815 - acc: 0.4698
Epoch 575/1000
381/381 [==============================] - 0s 97us/step - loss: 1.9786 - acc: 0.4672
Epoch 576/1000
381/381 [==============================] - 0s 100us/step - loss: 1.9748 - acc: 0.4672
Epoch 577/1000
381/381 [==============================] - 0s 95us/step - loss: 1.9756 - acc: 0.4619
Epoch 578/1000
381/381 [==============================] - 0s 106us/step - loss: 1.9750 - acc: 0.4646
Epoch 57

381/381 [==============================] - 0s 109us/step - loss: 1.9317 - acc: 0.4724
Epoch 732/1000
381/381 [==============================] - 0s 113us/step - loss: 1.9336 - acc: 0.4803
Epoch 733/1000
381/381 [==============================] - 0s 97us/step - loss: 1.9336 - acc: 0.4751
Epoch 734/1000
381/381 [==============================] - 0s 103us/step - loss: 1.9315 - acc: 0.4751
Epoch 735/1000
381/381 [==============================] - 0s 100us/step - loss: 1.9312 - acc: 0.4803
Epoch 736/1000
381/381 [==============================] - 0s 107us/step - loss: 1.9314 - acc: 0.4777
Epoch 737/1000
381/381 [==============================] - 0s 107us/step - loss: 1.9312 - acc: 0.4777
Epoch 738/1000
381/381 [==============================] - 0s 108us/step - loss: 1.9314 - acc: 0.4777
Epoch 739/1000
381/381 [==============================] - 0s 112us/step - loss: 1.9285 - acc: 0.4777
Epoch 740/1000
381/381 [==============================] - 0s 92us/step - loss: 1.9302 - acc: 0.4777
Epoch 7

381/381 [==============================] - 0s 100us/step - loss: 1.8831 - acc: 0.4856
Epoch 894/1000
381/381 [==============================] - 0s 118us/step - loss: 1.8820 - acc: 0.4856
Epoch 895/1000
381/381 [==============================] - 0s 105us/step - loss: 1.8876 - acc: 0.4882
Epoch 896/1000
381/381 [==============================] - 0s 112us/step - loss: 1.8848 - acc: 0.4856
Epoch 897/1000
381/381 [==============================] - 0s 119us/step - loss: 1.8830 - acc: 0.4856
Epoch 898/1000
381/381 [==============================] - 0s 118us/step - loss: 1.8828 - acc: 0.4856
Epoch 899/1000
381/381 [==============================] - 0s 102us/step - loss: 1.8815 - acc: 0.4856
Epoch 900/1000
381/381 [==============================] - 0s 107us/step - loss: 1.8835 - acc: 0.4882
Epoch 901/1000
381/381 [==============================] - 0s 106us/step - loss: 1.8798 - acc: 0.4882
Epoch 902/1000
381/381 [==============================] - 0s 122us/step - loss: 1.8831 - acc: 0.4829
Epoch

In [40]:
combined_model.summary()

__________________________________________________________________________________________________
Layer (type)                    Output Shape         Param #     Connected to                     
label_ip (InputLayer)           (None, 5)            0                                            
__________________________________________________________________________________________________
dec_feat_ip (InputLayer)        (None, 5, 117)       0                                            
__________________________________________________________________________________________________
gru_seq (GRU)                   (None, 5)            1845        dec_feat_ip[0][0]                
                                                                 label_ip[0][0]                   
__________________________________________________________________________________________________
cat (Concatenate)               (None, 10)           0           label_ip[0][0]                   
          

In [ ]:
def predict(x):
    latent_dim = 5
    x_f = x.reshape(1, feature_size)
    token = 'S'
    cont = True
    path = [token]
    x_path = np.zeros((1, paths_maxlen, path_vocab_size), dtype=np.bool)

    x_latent = get_hidden_x(x_f, model=label_model)
    x_latent = x_latent.reshape(1, latent_dim)
    x_path[0, 0, label_indices[token]] = 1
    pred = label_model.predict(x_f)
    label = [np.argmax(pred[0])]
    index = 1
    while cont & (index < paths_maxlen):
        pred = combined_model.predict([x_latent, x_path])
        char_index = np.argmax(pred[0])
        x_path[0, index, char_index] = 1
        next_char = indices_label[char_index]
        path.append(next_char)
        index += 1
        if next_char == 'E':
            cont = False
        # elif index == self.paths_maxlen - 1:
        #     path.append('E')

    if path[-1] != 'E':
        path.append('E')

    return [path, label]

### Path invariance method

In [42]:
def check_path(path): # Returns -1 if path traversed is wrong/non-existant
    # path = ''.join(path)
    path = path[1:-1]
    pred_features = []
    path_as_strings = []
    for i in range(len(path)):
        pred_features.append(int(path[i][:-1]))
        path_as_strings.append(path[i][-1])
        # if i%2 == 0:
        #     print('i -- ', i)
        #     print('path -- ', path)
        #     print('path[i] -- ', path[i])
        #     pred_features.append(int(path[i]))
        # else:
        #     path_as_strings.append(path[i])

    n_nodes = self.clf.tree_.node_count
    children_left = self.clf.tree_.children_left
    children_right = self.clf.tree_.children_right
    feature = self.clf.tree_.feature

    is_leaves = np.zeros(shape=n_nodes, dtype=bool)
    stack = [(0, -1)]
    while len(stack) > 0:
        node_id, parent_depth = stack.pop()
        # node_depth[node_id] = parent_depth + 1

        if (children_left[node_id] != children_right[node_id]):
            stack.append((children_left[node_id], parent_depth + 1))
            stack.append((children_right[node_id], parent_depth + 1))
        else:
            is_leaves[node_id] = True


    node = 0
    pred_target = -1
    subset_path = False
    for i in range(len(path_as_strings)):
        if path_as_strings[i] == 'L':
            if feature[node]+1 == pred_features[i]:
                node = children_left[node]
            # else:
                # pred_target = -1 # Remove for "subset" checks
                # break
        elif path_as_strings[i] == 'R':
            if feature[node]+1 == pred_features[i]:
                node = children_right[node]
            # else:
                # pred_target = -1 # Remove for "subset" checks
                # break
        if is_leaves[node]:
            for i, x in enumerate(self.clf.tree_.value[node][0]):
                if x > 0:
                    pred_target = i
            if i < len(path_as_strings):
                subset_path = True

    return pred_target, subset_path

In [43]:
path_df

new_col
0               1G0
1               3J0
2               1U0
3              1AC0
4               1N0
5              1AO0
6               2Y1
7               1G0
8              3AK0
9               1V0
10              3R0
11              3J0
12              3R0
13             3BJ0
14              3Y0
15              3X0
16              1V0
17         3F0,1BM0
18        1BU0,3BR0
19          3F0,1G0
20              1O0
21             3BJ0
22         1V0,1AH0
23              1O0
24         3F0,1AO0
25         3U0,1AO0
26             3AK0
27             1AC0
28          3F0,1G0
29              2E1
..              ...
120             3U1
121         3Y1,3U1
122        2L0,1DM1
123        1AO1,1P1
124            3CX1
125             3F1
126  2AT0,4AQ1,1AD0
127        2Y1,1BF1
128       2AM0,1DS1
129            4AF1
130            4AF1
131            1DI1
132       3BR1,1AV1
133             3T1
134       1CE1,3AH1
135            4BG1
136        1N1,1AV1
137        2AG0,3T1
138         3S1,3T1
139             1P1
140            4AQ1
141            4AQ1
142       1CE1,3CX1
143        1AO1,3U1
144        1AZ1,3U1
145            4BZ1
146       1AC1,3AY1
147            1AO1
148         1V1,3F1
149             3U1

[150 rows x 1 columns]

### Test model configuration

In [44]:
def score():
    count = []
    bleu_score = []
    j_coeff = []
    l_dist = []
    path_mismatch_count = []
    traverse_check_count = []
    order_mismatch_count = []
    subset_path_count = []
    for i in range(test_data.shape[0]):
        curr_feat = np.array([test_data.iloc[i, 0:X.shape[1]]])
        path, label = predict(curr_feat)
        actual_path = test_data.iloc[i, -1]

        actual_path_tok = [label_indices[char] for char in actual_path]
        pred_path_tok = [label_indices[char] for char in path]

        # j_coeff.append(super().get_j_coeff(actual_path_tok, pred_path_tok))

        print('actual vs predicted: ', test_data.iloc[i, -1], ' vs ', ' '.join(
            path), 'labels: ', y[i], label[0])
        count.append(y[i] == label[0])
        # print('Actual path -- ', actual_path)
        # print('Pred path -- ', path)
#         if actual_path != path:
#             print(' -- Path mismatch -- ')
#             if sorted(actual_path) == sorted(path):
#                 print(' -- Order mismatch -- ')
#                 order_mismatch_count.append(1)
#             else:
#                 path_mismatch_count.append(1)
#                 pred_target, subset_path = self.check_path(path)
#                 subset_path_count.append(subset_path)
#                 if pred_target != -1 and pred_target == self.df.iloc[i, self.X.shape[1]+1]:
#                     traverse_check_count.append(1)


        path = list(''.join(path))
        actual_path = list(''.join(test_data.iloc[i, -1]))
        bleu_score.append(sentence_bleu([actual_path], path))

#         lev_path = []
#         for i in range(len(path)):
#             if i in ['S','L','R','E']:
#                 lev_path.append(i)
#         l_dist.append(distance.levenshtein(
#             self.df.iloc[i, self.X.shape[1]].replace(' ', ''), ''.join(lev_path)))


    print('\nLabel accuracy - ', np.mean(count))
#     print('Path metric (Jaccard) - ', np.mean(j_coeff))
#     print('Path metric (Levenshtein) - ', np.mean(l_dist))
#     print('Path mismatch count - ', np.sum(path_mismatch_count))
#     print('Right traverse count - ', np.sum(traverse_check_count))
#     print('Order mismatch count - ', np.sum(order_mismatch_count))
#     print('Subset path count - ', np.sum(subset_path_count))
    print('Bleu score of paths - ', np.mean(bleu_score))

In [45]:
score()

actual vs predicted:  ['S', '1G0', 'E']  vs  S 3F0 1G0 E labels:  0 0
actual vs predicted:  ['S', '3J0', 'E']  vs  S 3F0 1G0 E labels:  0 0
actual vs predicted:  ['S', '1U0', 'E']  vs  S 3F0 1G0 E labels:  0 0


/home/shakkeel/anaconda3/envs/test_imly/lib/python3.6/site-packages/nltk/translate/bleu_score.py:523: UserWarning: 
The hypothesis contains 0 counts of 3-gram overlaps.
Therefore the BLEU score evaluates to 0, independently of
how many N-gram overlaps of lower order it contains.
Consider using lower n-gram order or use SmoothingFunction()
  warnings.warn(_msg)
/home/shakkeel/anaconda3/envs/test_imly/lib/python3.6/site-packages/nltk/translate/bleu_score.py:523: UserWarning: 
The hypothesis contains 0 counts of 4-gram overlaps.
Therefore the BLEU score evaluates to 0, independently of
how many N-gram overlaps of lower order it contains.
Consider using lower n-gram order or use SmoothingFunction()
  warnings.warn(_msg)


actual vs predicted:  ['S', '1AC0', 'E']  vs  S 3F0 1G0 E labels:  0 0
actual vs predicted:  ['S', '1N0', 'E']  vs  S 3F0 1G0 E labels:  0 0
actual vs predicted:  ['S', '1AO0', 'E']  vs  S 3F0 1G0 E labels:  0 0
actual vs predicted:  ['S', '2Y1', 'E']  vs  S 3F0 1G0 E labels:  0 0
actual vs predicted:  ['S', '1G0', 'E']  vs  S 3F0 1G0 E labels:  0 0
actual vs predicted:  ['S', '3AK0', 'E']  vs  S 3F0 1G0 E labels:  0 0


/home/shakkeel/anaconda3/envs/test_imly/lib/python3.6/site-packages/nltk/translate/bleu_score.py:523: UserWarning: 
The hypothesis contains 0 counts of 2-gram overlaps.
Therefore the BLEU score evaluates to 0, independently of
how many N-gram overlaps of lower order it contains.
Consider using lower n-gram order or use SmoothingFunction()
  warnings.warn(_msg)


actual vs predicted:  ['S', '1V0', 'E']  vs  S 3F0 1G0 E labels:  0 0
actual vs predicted:  ['S', '3R0', 'E']  vs  S 3F0 1G0 E labels:  0 0
actual vs predicted:  ['S', '3J0', 'E']  vs  S 3F0 1G0 E labels:  0 0
actual vs predicted:  ['S', '3R0', 'E']  vs  S 3F0 1G0 E labels:  0 0
actual vs predicted:  ['S', '3BJ0', 'E']  vs  S 3F0 1G0 E labels:  0 0
actual vs predicted:  ['S', '3Y0', 'E']  vs  S 3F0 1G0 E labels:  0 0
actual vs predicted:  ['S', '3X0', 'E']  vs  S 3F0 1G0 E labels:  0 0
actual vs predicted:  ['S', '1V0', 'E']  vs  S 3F0 1G0 E labels:  0 0
actual vs predicted:  ['S', '3F0', '1BM0', 'E']  vs  S 3F0 1G0 E labels:  0 0
actual vs predicted:  ['S', '1BU0', '3BR0', 'E']  vs  S 3F0 1G0 E labels:  0 0
actual vs predicted:  ['S', '3F0', '1G0', 'E']  vs  S 3F0 1G0 E labels:  0 0
actual vs predicted:  ['S', '1O0', 'E']  vs  S 3F0 1G0 E labels:  0 0
actual vs predicted:  ['S', '3BJ0', 'E']  vs  S 3F0 1G0 E labels:  0 0
actual vs predicted:  ['S', '1V0', '1AH0', 'E']  vs  S 3F0 1G0 E

actual vs predicted:  ['S', '1BU1', 'E']  vs  S 1AO1 1AV1 E labels:  2 2
actual vs predicted:  ['S', '1AO1', '1DG0', '2J0', 'E']  vs  S 1AO1 3U1 E labels:  2 2
actual vs predicted:  ['S', '3U1', 'E']  vs  S 1AO1 1AV1 E labels:  2 2
actual vs predicted:  ['S', '3Y1', '3U1', 'E']  vs  S 1AO1 1AV1 E labels:  2 2
actual vs predicted:  ['S', '2L0', '1DM1', 'E']  vs  S 1AO1 1AV1 E labels:  2 2
actual vs predicted:  ['S', '1AO1', '1P1', 'E']  vs  S 1AO1 3U1 E labels:  2 2
actual vs predicted:  ['S', '3CX1', 'E']  vs  S 1AO1 1AV1 E labels:  2 2
actual vs predicted:  ['S', '3F1', 'E']  vs  S 1AO1 3U1 E labels:  2 2
actual vs predicted:  ['S', '2AT0', '4AQ1', '1AD0', 'E']  vs  S 1AO1 1AC1 E labels:  2 2
actual vs predicted:  ['S', '2Y1', '1BF1', 'E']  vs  S 3T1 E labels:  2 1
actual vs predicted:  ['S', '2AM0', '1DS1', 'E']  vs  S 1AO1 1AV1 E labels:  2 2
actual vs predicted:  ['S', '4AF1', 'E']  vs  S 1O1 3CX0 E labels:  2 1
actual vs predicted:  ['S', '4AF1', 'E']  vs  S 1AO1 1AV1 E labels:  2

## Path invariance trials using rpart -- generic

In [46]:
## Import nnum, vnum, nodes, csplit, split_df,
## frame

splits = pd.read_csv('../../data/raw/splits.csv', delimiter=",", index_col=0)
csplit = pd.read_csv('../../data/raw/csplit.csv', delimiter=",")
frame = pd.read_csv('../../data/raw/frame.csv', delimiter=",",index_col=0)

# frame = frame.drop(["Unnamed: 0"], axis=1)
frame = frame.rename(columns={"var": "variable"})
# bin_labels = bin_labels.rename(columns={"Unnamed: 0": "label", "label_list": "bins"})

In [47]:
frame

variable    n   wt  dev  yval  complexity  ncompete  nsurrogate  \
1   Petal.Length  150  150  100     1       0.500         3           3   
2         <leaf>   50   50    0     1       0.000         0           0   
3    Petal.Width  100  100   50     2       0.440         3           3   
6   Petal.Length   54   54    5     2       0.020         3           0   
12   Petal.Width   48   48    1     2       0.010         3           0   
24        <leaf>   47   47    0     2       0.000         0           0   
25        <leaf>    1    1    0     3       0.000         0           0   
13   Petal.Width    6    6    2     3       0.010         3           2   
26  Sepal.Length    3    3    1     2       0.010         3           0   
52        <leaf>    2    2    0     2       0.000         0           0   
53        <leaf>    1    1    0     3       0.000         0           0   
27        <leaf>    3    3    0     3       0.000         0           0   
7   Petal.Length   46   46    1     3       0.005         3           0   
14  Sepal.Length    3    3    1     3       0.005         1           0   
28        <leaf>    1    1    0     2       0.000         0           0   
29        <leaf>    2    2    0     3       0.000         0           0   
15        <leaf>   43   43    0     3       0.000         0           0   

    yval2.  yval2..1  yval2..2  yval2..3  yval2..4  yval2..5  yval2..6  \
1      1.0      50.0      50.0      50.0  0.333333  0.333333  0.333333   
2      1.0      50.0       0.0       0.0  1.000000  0.000000  0.000000   
3      2.0       0.0      50.0      50.0  0.000000  0.500000  0.500000   
6      2.0       0.0      49.0       5.0  0.000000  0.907407  0.092593   
12     2.0       0.0      47.0       1.0  0.000000  0.979167  0.020833   
24     2.0       0.0      47.0       0.0  0.000000  1.000000  0.000000   
25     3.0       0.0       0.0       1.0  0.000000  0.000000  1.000000   
13     3.0       0.0       2.0       4.0  0.000000  0.333333  0.666667   
26     2.0       0.0       2.0       1.0  0.000000  0.666667  0.333333   
52     2.0       0.0       2.0       0.0  0.000000  1.000000  0.000000   
53     3.0       0.0       0.0       1.0  0.000000  0.000000  1.000000   
27     3.0       0.0       0.0       3.0  0.000000  0.000000  1.000000   
7      3.0       0.0       1.0      45.0  0.000000  0.021739  0.978261   
14     3.0       0.0       1.0       2.0  0.000000  0.333333  0.666667   
28     2.0       0.0       1.0       0.0  0.000000  1.000000  0.000000   
29     3.0       0.0       0.0       2.0  0.000000  0.000000  1.000000   
15     3.0       0.0       0.0      43.0  0.000000  0.000000  1.000000   

    yval2.nodeprob  
1         1.000000  
2         0.333333  
3         0.666667  
6         0.360000  
12        0.320000  
24        0.313333  
25        0.006667  
13        0.040000  
26        0.020000  
52        0.013333  
53        0.006667  
27        0.020000  
7         0.306667  
14        0.020000  
28        0.006667  
29        0.013333  
15        0.286667

In [59]:
## Generate nnum, vnum, nodes(split_df and csplit - 2L if necessary)

temp_frame = frame

nc = temp_frame[["ncompete", "nsurrogate"]]

index = np.cumsum((frame[["variable"]]!="<leaf>").values + nc[["ncompete"]].values + nc[["nsurrogate"]].values)

index_df = pd.DataFrame((np.insert(index,0,0)+1)[:-1], columns=["i"], index=frame.index)

temp_frame = pd.concat([temp_frame, index_df], axis=1)

# temp_frame[temp_frame[["var"]]=="<leaf>"]
# temp_frame.where(temp_frame[["var"]]=="<leaf>")
# temp_frame.loc[temp_frame[["variable"]]=="<leaf>", "index"] = 0
temp_frame.i[temp_frame.variable == "<leaf>"] = 0

/home/shakkeel/anaconda3/envs/test_imly/lib/python3.6/site-packages/ipykernel_launcher.py:16: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  app.launch_new_instance()


In [60]:
temp_frame

variable    n   wt  dev  yval  complexity  ncompete  nsurrogate  \
1   Petal.Length  150  150  100     1       0.500         3           3   
2         <leaf>   50   50    0     1       0.000         0           0   
3    Petal.Width  100  100   50     2       0.440         3           3   
6   Petal.Length   54   54    5     2       0.020         3           0   
12   Petal.Width   48   48    1     2       0.010         3           0   
24        <leaf>   47   47    0     2       0.000         0           0   
25        <leaf>    1    1    0     3       0.000         0           0   
13   Petal.Width    6    6    2     3       0.010         3           2   
26  Sepal.Length    3    3    1     2       0.010         3           0   
52        <leaf>    2    2    0     2       0.000         0           0   
53        <leaf>    1    1    0     3       0.000         0           0   
27        <leaf>    3    3    0     3       0.000         0           0   
7   Petal.Length   46   46    1     3       0.005         3           0   
14  Sepal.Length    3    3    1     3       0.005         1           0   
28        <leaf>    1    1    0     2       0.000         0           0   
29        <leaf>    2    2    0     3       0.000         0           0   
15        <leaf>   43   43    0     3       0.000         0           0   

    yval2.  yval2..1  yval2..2  yval2..3  yval2..4  yval2..5  yval2..6  \
1      1.0      50.0      50.0      50.0  0.333333  0.333333  0.333333   
2      1.0      50.0       0.0       0.0  1.000000  0.000000  0.000000   
3      2.0       0.0      50.0      50.0  0.000000  0.500000  0.500000   
6      2.0       0.0      49.0       5.0  0.000000  0.907407  0.092593   
12     2.0       0.0      47.0       1.0  0.000000  0.979167  0.020833   
24     2.0       0.0      47.0       0.0  0.000000  1.000000  0.000000   
25     3.0       0.0       0.0       1.0  0.000000  0.000000  1.000000   
13     3.0       0.0       2.0       4.0  0.000000  0.333333  0.666667   
26     2.0       0.0       2.0       1.0  0.000000  0.666667  0.333333   
52     2.0       0.0       2.0       0.0  0.000000  1.000000  0.000000   
53     3.0       0.0       0.0       1.0  0.000000  0.000000  1.000000   
27     3.0       0.0       0.0       3.0  0.000000  0.000000  1.000000   
7      3.0       0.0       1.0      45.0  0.000000  0.021739  0.978261   
14     3.0       0.0       1.0       2.0  0.000000  0.333333  0.666667   
28     2.0       0.0       1.0       0.0  0.000000  1.000000  0.000000   
29     3.0       0.0       0.0       2.0  0.000000  0.000000  1.000000   
15     3.0       0.0       0.0      43.0  0.000000  0.000000  1.000000   

    yval2.nodeprob   i  
1         1.000000   1  
2         0.333333   0  
3         0.666667   8  
6         0.360000  15  
12        0.320000  19  
24        0.313333   0  
25        0.006667   0  
13        0.040000  23  
26        0.020000  29  
52        0.013333   0  
53        0.006667   0  
27        0.020000   0  
7         0.306667  33  
14        0.020000  37  
28        0.006667   0  
29        0.013333   0  
15        0.286667   0

In [61]:
nodes = temp_frame[["n", "ncompete", "nsurrogate", "i"]]

In [62]:
nnum = list(temp_frame.index) # row names of temp_frame

In [63]:
feature_names = ["Sepal.Length", "Sepal.Width", "Petal.Length", "Petal.Width"]

vnum = list(map(feature_names.index, splits.index))

In [64]:
nodes

n  ncompete  nsurrogate   i
1   150         3           3   1
2    50         0           0   0
3   100         3           3   8
6    54         3           0  15
12   48         3           0  19
24   47         0           0   0
25    1         0           0   0
13    6         3           2  23
26    3         3           0  29
52    2         0           0   0
53    1         0           0   0
27    3         0           0   0
7    46         3           0  33
14    3         1           0  37
28    1         0           0   0
29    2         0           0   0
15   43         0           0   0

In [80]:
nnum

[1, 2, 3, 6, 12, 24, 25, 13, 26, 52, 53, 27, 7, 14, 28, 29, 15]

In [81]:
def return_yval(path): # [1,0,0,0]
    node = 0
    nspl = 1
    i = 0
    while nspl != 0:
        npos = nnum[node] # i)0, 
        nspl = nodes.iloc[npos-1][3] # i)1
        var = vnum[nspl]
        # ncat
        temp = splits.iloc[nspl][3]
        if nspl > 0:
            print("nspl succeeded")
            if path[i] == 0: # i)1
                direction = -1
                i+=1
            else:
                direction = 1
                i+=1

            if direction == -1:
                print(node)
                if node == 0:
                    node = 1
                node = 2 * node
            else:
                print(node)
                if node == 0:
                    node = 1
                node = 2 * node + 1
            if len(path) == 1:
                nspl = 0
        else:
            print('nspl failed')
            print("leaf node -- ", node)
            yval = temp_frame.iloc[node][4]
    return temp_frame.iloc[node][4]

In [77]:
nodes.iloc[0]

n             150
ncompete        3
nsurrogate      3
i               1
Name: 1, dtype: int64

In [86]:

path = [1,1,0,1]
a = [1,0,0,0]
b = [1,1,1]
c = [0]
d = [1,1,1,1,1,1,0]
e = [1,0,1,0,0]
return_yval(e)

nspl succeeded
0
nspl failed
leaf node --  3


2

In [30]:
temp_frame

variable    n   wt  dev  yval  complexity  ncompete  nsurrogate  \
0   Petal.Length  150  150  100     1       0.500         3           3   
1         <leaf>   50   50    0     1       0.000         0           0   
2    Petal.Width  100  100   50     2       0.440         3           3   
3   Petal.Length   54   54    5     2       0.020         3           0   
4    Petal.Width   48   48    1     2       0.010         3           0   
5         <leaf>   47   47    0     2       0.000         0           0   
6         <leaf>    1    1    0     3       0.000         0           0   
7    Petal.Width    6    6    2     3       0.010         3           2   
8   Sepal.Length    3    3    1     2       0.010         3           0   
9         <leaf>    2    2    0     2       0.000         0           0   
10        <leaf>    1    1    0     3       0.000         0           0   
11        <leaf>    3    3    0     3       0.000         0           0   
12  Petal.Length   46   46    1     3       0.005         3           0   
13  Sepal.Length    3    3    1     3       0.005         1           0   
14        <leaf>    1    1    0     2       0.000         0           0   
15        <leaf>    2    2    0     3       0.000         0           0   
16        <leaf>   43   43    0     3       0.000         0           0   

    yval2.  yval2..1  yval2..2  yval2..3  yval2..4  yval2..5  yval2..6  \
0      1.0      50.0      50.0      50.0  0.333333  0.333333  0.333333   
1      1.0      50.0       0.0       0.0  1.000000  0.000000  0.000000   
2      2.0       0.0      50.0      50.0  0.000000  0.500000  0.500000   
3      2.0       0.0      49.0       5.0  0.000000  0.907407  0.092593   
4      2.0       0.0      47.0       1.0  0.000000  0.979167  0.020833   
5      2.0       0.0      47.0       0.0  0.000000  1.000000  0.000000   
6      3.0       0.0       0.0       1.0  0.000000  0.000000  1.000000   
7      3.0       0.0       2.0       4.0  0.000000  0.333333  0.666667   
8      2.0       0.0       2.0       1.0  0.000000  0.666667  0.333333   
9      2.0       0.0       2.0       0.0  0.000000  1.000000  0.000000   
10     3.0       0.0       0.0       1.0  0.000000  0.000000  1.000000   
11     3.0       0.0       0.0       3.0  0.000000  0.000000  1.000000   
12     3.0       0.0       1.0      45.0  0.000000  0.021739  0.978261   
13     3.0       0.0       1.0       2.0  0.000000  0.333333  0.666667   
14     2.0       0.0       1.0       0.0  0.000000  1.000000  0.000000   
15     3.0       0.0       0.0       2.0  0.000000  0.000000  1.000000   
16     3.0       0.0       0.0      43.0  0.000000  0.000000  1.000000   

    yval2.nodeprob   i  
0         1.000000   1  
1         0.333333   0  
2         0.666667   8  
3         0.360000  15  
4         0.320000  19  
5         0.313333   0  
6         0.006667   0  
7         0.040000  23  
8         0.020000  29  
9         0.013333   0  
10        0.006667   0  
11        0.020000   0  
12        0.306667  33  
13        0.020000  37  
14        0.006667   0  
15        0.013333   0  
16        0.286667   0

In [33]:
splits

count  ncat    improve  index       adj
Petal.Length    150    -1  50.000000   2.45  0.000000
Petal.Width     150    -1  50.000000   0.80  0.000000
Sepal.Length    150    -1  34.164050   5.45  0.000000
Sepal.Width     150     1  19.038508   3.35  0.000000
Petal.Width       0    -1   1.000000   0.80  1.000000
Sepal.Length      0    -1   0.920000   5.45  0.760000
Sepal.Width       0     1   0.833333   3.35  0.500000
Petal.Width     100    -1  38.969404   1.75  0.000000
Petal.Length    100    -1  37.353535   4.75  0.000000
Sepal.Length    100    -1  10.686869   6.15  0.000000
Sepal.Width     100    -1   3.555556   2.45  0.000000
Petal.Length      0    -1   0.910000   4.75  0.804348
Sepal.Length      0    -1   0.730000   6.15  0.413043
Sepal.Width       0    -1   0.670000   2.95  0.282609
Petal.Length     54    -1   4.449074   4.95  0.000000
Sepal.Length     54    -1   1.677848   7.10  0.000000
Petal.Width      54    -1   0.997151   1.35  0.000000
Sepal.Width      54     1   0.250014   2.65  0.000000
Petal.Width      48    -1   1.958333   1.65  0.000000
Sepal.Length     48     1   0.958333   4.95  0.000000
Sepal.Width      48     1   0.101190   2.55  0.000000
Petal.Length     48    -1   0.063596   4.45  0.000000
Petal.Width       6     1   1.333333   1.55  0.000000
Sepal.Width       6     1   0.666667   2.65  0.000000
Petal.Length      6    -1   0.666667   5.35  0.000000
Sepal.Length      6    -1   0.266667   6.95  0.000000
Sepal.Length      0     1   0.833333   6.50  0.666667
Sepal.Width       0     1   0.833333   2.65  0.666667
Sepal.Length      3    -1   1.333333   6.95  0.000000
Petal.Length      3    -1   1.333333   5.45  0.000000
Sepal.Width       3    -1   0.333333   2.85  0.000000
Petal.Width       3     1   0.333333   1.65  0.000000
Petal.Length     46    -1   0.623188   4.85  0.000000
Sepal.Length     46    -1   0.242236   5.95  0.000000
Petal.Width      46    -1   0.123188   1.85  0.000000
Sepal.Width      46     1   0.099379   3.15  0.000000
Sepal.Length      3    -1   1.333333   5.95  0.000000
Sepal.Width       3     1   1.333333   3.10  0.000000

In [96]:
iris.target_names

array(['setosa', 'versicolor', 'virginica'], dtype='<U10')

#### Bin reduction trials

In [31]:
def get_bin_mappings(flow_matrix_dim, emd_index):
    # mapping_list = []
    mapping_dict = {}
    for i in range(flow_matrix_dim):
        for j in range(flow_matrix_dim):
            if emd_trials[emd_index]['flow_matrix'][i][j] != 0.0:
                # mapping_list.append([emd_trials[emd_index]['flow_matrix'][i][j], (i,j)])
                deep_set(mapping_dict, [i, j], emd_trials[emd_index]['flow_matrix'][i][j])
                
    return mapping_dict

In [21]:
import pyemd
import random
from sklearn.preprocessing import normalize
from scipy.spatial import distance as scipy_distance
from copy import copy
import numpy as np

# actual_bins = sorted([2.4, 5.4, 1.6, 9.7, 8.9])
actual_bins = sorted([17.8, 2.4, 5.4, 1.6, 9.7, 8.9, 11.3, 0.5, 3.3, 15.3])
# actual_freq = [10.0, 3.0, 4.0, 1.0, 5.0]
# actual_freq = normalize([actual_freq])
# actual_freq = actual_freq.tolist()[0]

# 1) Choosing reduced bins by random sampling
# 2) How to choose frequency of new bins?
#   - Uniform values
#   - Kernels
# 3) Obj func to retrieve reduced bins
# ext_bins = random.sample(actual_bins, 3)
# ext_bins

In [120]:
## Pyemd approach -- continuous var
dist_list = []
emd_trials = {}
for index in range(1000):
    ext_bins = sorted(np.random.uniform(actual_bins[0],actual_bins[-1], 3))
    ext_freq = []
    # actual_freq = [10.0, 3.0, 4.0, 1.0, 5.0]
    actual_freq = [10.0, 3.0, 4.0, 1.0, 5.0, 10.0, 3.0, 4.0, 1.0, 5.0]
    actual_freq_norm = normalize([actual_freq], norm='l1').reshape(10,)
    for i, x in enumerate(ext_bins):
        new_freq = []
        for j, b in enumerate(actual_bins):
            c = 1/(np.sqrt(2*np.pi))
            # dist = -(((x-b)**2)/2)
            dist = -((np.power((x-b),2))/2)
            d = np.exp(dist)
            w = c * d
            new_freq.append(w * actual_freq[j])
        ext_freq.append(sum(new_freq))

    combined_bins = copy(actual_bins)
    for _, val in enumerate(ext_bins):
        combined_bins.append(val)

    dist_matrix = np.zeros((13,13), dtype='float64')
    ## Distance
    for i, val in enumerate(combined_bins):
        for j, val_2 in enumerate(combined_bins):
            dist_matrix[i,j] = scipy_distance.euclidean(combined_bins[i], combined_bins[j])
    
    ext_freq_norm = normalize([ext_freq], norm='l1').reshape(3,)
    
    for i in range(len(actual_freq)):
        # ext_freq.insert(0, 0.0)
        ext_freq_norm = np.insert(ext_freq_norm, 0, 0.0)

    for i in range(len(ext_bins)):
        # actual_freq.append(0.0)
        actual_freq_norm = np.append(actual_freq_norm, 0.0)

    # ext_freq = np.array(ext_freq)    
    # actual_freq = np.array(actual_freq)
    
    emd_val, min_cost_flow = pyemd.emd_with_flow(actual_freq_norm, ext_freq_norm, dist_matrix)
    dist_list.append(emd_val)
    emd_trials.update({index:{'distance':emd_val, 'flow_matrix':min_cost_flow,
                             'actual_bins':actual_bins, 'actual_freq_norm':actual_freq_norm,
                             'ext_bins':ext_bins, 'ext_freq_norm':ext_freq_norm,
                             'dist_matrix': dist_matrix}})

In [121]:
actual_freq

[10.0, 3.0, 4.0, 1.0, 5.0, 10.0, 3.0, 4.0, 1.0, 5.0]

In [122]:
ext_freq

[1.3162660158574675, 0.5209963676861593, 2.009792259447329]

In [123]:
actual_freq_norm

array([0.2173913 , 0.06521739, 0.08695652, 0.02173913, 0.10869565,
       0.2173913 , 0.06521739, 0.08695652, 0.02173913, 0.10869565,
       0.        , 0.        , 0.        ])

In [124]:
ext_freq_norm

array([0.        , 0.        , 0.        , 0.        , 0.        ,
       0.        , 0.        , 0.        , 0.        , 0.        ,
       0.34214903, 0.13542734, 0.52242363])

In [125]:
min(dist_list)

1.2111874752214022

In [126]:
dist_list.index(min(dist_list))

425

In [128]:
emd_trials[425]['actual_bins']

[0.5, 1.6, 2.4, 3.3, 5.4, 8.9, 9.7, 11.3, 15.3, 17.8]

In [129]:
emd_trials[425]['ext_bins']

[0.9385060907250806, 9.345561451682828, 17.111083893285034]

In [131]:
for i in range(13):
    for j in range(13):
        if emd_trials[425]['flow_matrix'][i][j] != 0.0:
            print(emd_trials[425]['flow_matrix'][i][j], (i,j))

0.217391 (0, 10)
0.065217 (1, 10)
0.086957 (2, 10)
0.021739 (3, 10)
0.046495 (4, 10)
0.062201 (4, 11)
0.217391 (5, 11)
0.065217 (6, 11)
0.077296 (7, 11)
0.009661 (7, 12)
0.021739 (8, 12)
0.108696 (9, 12)


In [99]:
emd_trials[6017] ## w/ 10,000 trials

{'distance': 0.23798528644410086,
 'flow_matrix': [[0.0, 0.0, 0.0, 0.0, 0.0, 0.434783, 0.0, 0.0],
  [0.0, 0.0, 0.0, 0.0, 0.0, 0.124277, 0.006158, 0.0],
  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.173913, 0.0],
  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.005357, 0.038121],
  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.217391],
  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0],
  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0],
  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]],
 'actual_bins': [1.6, 2.4, 5.4, 8.9, 9.7],
 'actual_freq_norm': array([0.43478261, 0.13043478, 0.17391304, 0.04347826, 0.2173913 ,
        0.        , 0.        , 0.        ]),
 'ext_bins': [1.6064817771506419, 5.393405228969593, 9.322409378281648],
 'ext_freq_norm': array([0.        , 0.        , 0.        , 0.        , 0.        ,
        0.55905953, 0.18542895, 0.25551153]),
 'dist_matrix': array([[0.00000000e+00, 8.00000000e-01, 3.80000000e+00, 7.30000000e+00,
         8.10000000e+00, 6.48177715e-03, 3.79340523e+00, 7.72240938e+00],
        [8.00000000e

In [75]:
emd_trials[562] ## w/ 1000 trials

{'distance': 0.2447755192305009,
 'flow_matrix': [[0.0, 0.0, 0.0, 0.0, 0.0, 0.434783, 0.0, 0.0],
  [0.0, 0.0, 0.0, 0.0, 0.0, 0.124085, 0.00635, 0.0],
  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.173062, 0.000851],
  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.043478],
  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.217391],
  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0],
  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0],
  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]],
 'ext_bin': [1.669313785130966, 5.607383172387225, 9.530849925961318],
 'ext_freq': [4.897789781010717, 1.5723296165685663, 2.2936506762020716],
 'dist_matrix': array([[0.        , 0.8       , 3.8       , 7.3       , 8.1       ,
         0.06931379, 4.00738317, 7.93084993],
        [0.8       , 0.        , 3.        , 6.5       , 7.3       ,
         0.73068621, 3.20738317, 7.13084993],
        [3.8       , 3.        , 0.        , 3.5       , 4.3       ,
         3.73068621, 0.20738317, 4.13084993],
        [7.3       , 6.5       , 3.5       , 0.        , 0.8

In [101]:
emd_trials[6017]['flow_matrix']

[[0.0, 0.0, 0.0, 0.0, 0.0, 0.434783, 0.0, 0.0],
 [0.0, 0.0, 0.0, 0.0, 0.0, 0.124277, 0.006158, 0.0],
 [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.173913, 0.0],
 [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.005357, 0.038121],
 [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.217391],
 [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0],
 [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0],
 [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]]

In [105]:
emd_trials[6017]['flow_matrix'][1][1] != 0.0

False

In [106]:
for i in range(8):
    for j in range(8):
        if emd_trials[6017]['flow_matrix'][i][j] != 0.0:
            print(emd_trials[6017]['flow_matrix'][i][j], (i,j))

0.434783 (0, 5)
0.124277 (1, 5)
0.006158 (1, 6)
0.173913 (2, 6)
0.005357 (3, 6)
0.038121 (3, 7)
0.217391 (4, 7)


In [108]:
emd_trials[6017]['actual_bins']

[1.6, 2.4, 5.4, 8.9, 9.7]

In [109]:
emd_trials[6017]['ext_bins']

[1.6064817771506419, 5.393405228969593, 9.322409378281648]

In [100]:
emd_trials

{0: {'distance': 2.1380404013343006,
  'flow_matrix': [[0.0, 0.0, 0.0, 0.0, 0.0, 0.2628, 0.171983, 0.0],
   [0.0, 0.0, 0.0, 0.0, 0.0, 0.130435, 0.0, 0.0],
   [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.173913, 0.0],
   [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.043478, 0.0],
   [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.036143, 0.181247],
   [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0],
   [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0],
   [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]],
  'actual_bins': [1.6, 2.4, 5.4, 8.9, 9.7],
  'actual_freq_norm': array([0.43478261, 0.13043478, 0.17391304, 0.04347826, 0.2173913 ,
         0.        , 0.        , 0.        ]),
  'ext_bins': [3.78925805791465, 4.685435402871269, 7.702180208333779],
  'ext_freq_norm': array([0.        , 0.        , 0.        , 0.        , 0.        ,
         0.39323538, 0.4255172 , 0.18124742]),
  'dist_matrix': array([[0.        , 0.8       , 3.8       , 7.3       , 8.1       ,
          2.18925806, 3.0854354 , 6.10218021],
         [0.8       , 0.        , 3. 

In [296]:
new_freq

[1.790667856900023,
 1.0738105227465606,
 0.06432139515484088,
 4.944241101512384e-09,
 1.4374118916223221e-10]

In [297]:
actual_bins

[1.6,
 2.4,
 5.4,
 8.9,
 9.7,
 2.196769471499167,
 5.8795597151350485,
 5.98261741551536]

In [341]:
emd_trials[dist_list.index(max(dist_list))]

{'distance': 175.8061351642649,
 'flow_matrix': [[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0],
  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0],
  [0.0, 0.0, 0.0, 0.0, 0.0, 0.533209, 0.518282, 0.0],
  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.5491940000000001],
  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0],
  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0],
  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0],
  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]],
 'ext_bin': [7.070223146830314, 7.115452473868924, 7.639984088218773],
 'ext_freq': array([0.        , 0.        , 0.        , 0.        , 0.        ,
        0.53320189, 0.5182754 , 0.54920463])}

In [342]:
emd_trials

{0: {'distance': 142.38472402642964,
  'flow_matrix': [[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0],
   [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0],
   [0.0, 0.0, 0.0, 0.0, 0.0, 1.613818, 0.0, 0.0],
   [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.999994, 0.0],
   [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.640918, 2.296642],
   [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0],
   [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0],
   [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]],
  'ext_bin': [5.362690351859676, 8.726272460942639, 9.61607149427512],
  'ext_freq': array([0.        , 0.        , 0.        , 0.        , 0.        ,
         1.61380982, 1.64091516, 2.29663962])},
 1: {'distance': 97.43179473427186,
  'flow_matrix': [[0.0, 0.0, 0.0, 0.0, 0.0, 4.899253, 4.913283, 0.0],
   [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0],
   [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 1.410406],
   [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0],
   [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0],
   [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0],
   [0.0, 0.0, 0.0, 0.0, 0.0, 0.

---

#### Trial 2 

In [22]:
def jaccard_score_inconsistent(x, y):
    intersection_cardinality = len(set.intersection(*[set(x), set(y)]))
    union_cardinality = len(set.union(*[set(x), set(y)]))
    return intersection_cardinality/float(union_cardinality)

def get_j_coeff(a, b):
    if len(a) != len(b):
        return jaccard_score_inconsistent(a, b)
    return jaccard_score(a, b, average='micro')

In [181]:
actual_bins = [['a'], ['b','c'], ['a','c'], ['b'], ['c']]
np.random.choice(actual_bins, 3, replace=False).tolist()

[['b'], ['b', 'c'], ['c']]

In [258]:
## Pyemd approach -- categorical var
'''
Max levels = 3; (a,b,c)
actual_bins = [(a), (b,c), (a,c), (b), (c)]
actual_freq = [10.0, 3.0, 4.0, 1.0, 5.0]
possible_out = [(a), (b), (c), (a,b), (a,c), (b,c)]
'''

actual_bins = [['a'], ['b','c'], ['a','c'], ['a','b'], ['c']]
possible_out = [['a'], ['b','c'], ['a','c'], ['a','b'], ['b'], ['c']]


dist_list = []
emd_trials = {}
for index in range(1000):
    ext_bins = np.random.choice(actual_bins, 3, replace=False).tolist()
    ext_freq = []
    # actual_freq = [10.0, 3.0, 4.0, 1.0, 5.0]
    actual_freq = [10.0, 3.0, 4.0, 1.0, 5.0]
    actual_freq_norm = normalize([actual_freq], norm='l1').reshape(5,)
    for i, x in enumerate(ext_bins):
        new_freq = []
        for j, b in enumerate(actual_bins):
            c = 1/(np.sqrt(2*np.pi))
            # dist = 1 - get_j_coeff(b, x) # Change distance metric
            dist = distance.levenshtein(b,x)
            dist = -((np.power(dist,2))/2)
            d = np.exp(dist)
            w = c * d
            new_freq.append(w * actual_freq[j])
        ext_freq.append(sum(new_freq))

    combined_bins = copy(actual_bins)
    for _, val in enumerate(ext_bins):
        combined_bins.append(val)

    dist_matrix = np.zeros((8,8), dtype='float64')
    ## Distance
    for i, val in enumerate(combined_bins):
        for j, val_2 in enumerate(combined_bins):
            # dist_matrix[i,j] = distance.euclidean(combined_bins[i], combined_bins[j])
            # dist_matrix[i,j] = get_j_coeff(combined_bins[i], combined_bins[j])
            dist_matrix[i,j] = distance.levenshtein(combined_bins[i], combined_bins[j])
    
    ext_freq_norm = normalize([ext_freq], norm='l1').reshape(3,)
    
    for i in range(len(actual_freq)):
        # ext_freq.insert(0, 0.0)
        ext_freq_norm = np.insert(ext_freq_norm, 0, 0.0)

    for i in range(len(ext_bins)):
        # actual_freq.append(0.0)
        actual_freq_norm = np.append(actual_freq_norm, 0.0)

    # ext_freq = np.array(ext_freq)    
    # actual_freq = np.array(actual_freq)
    
    emd_val, min_cost_flow = pyemd.emd_with_flow(actual_freq_norm, ext_freq_norm, dist_matrix)
    dist_list.append(emd_val)
    emd_trials.update({index:{'distance':emd_val, 'flow_matrix':min_cost_flow,
                             'actual_bins':actual_bins, 'actual_freq_norm':actual_freq_norm,
                             'ext_bins':ext_bins, 'ext_freq_norm':ext_freq_norm,
                             'dist_matrix': dist_matrix}})

In [235]:
??distance.levenshtein

In [193]:
len(ext_bins)

3

In [184]:
emd_trials

{0: {'distance': 0.21014473188400012,
  'flow_matrix': [[0.0, 0.0, 0.0, 0.0, 0.0, 0.144815, 0.0, 0.289968],
   [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.130435, 0.0],
   [0.0, 0.0, 0.0, 0.0, 0.0, 0.173913, 0.0, 0.0],
   [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.043478],
   [0.0, 0.0, 0.0, 0.0, 0.0, 0.026073, 0.191318, 0.0],
   [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0],
   [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0],
   [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]],
  'actual_bins': [['a'], ['b', 'c'], ['a', 'c'], ['b'], ['c']],
  'actual_freq_norm': array([0.43478261, 0.13043478, 0.17391304, 0.04347826, 0.2173913 ,
         0.        , 0.        , 0.        ]),
  'ext_bins': [['b', 'c'], ['a', 'c'], ['c']],
  'ext_freq_norm': array([0.        , 0.        , 0.        , 0.        , 0.        ,
         0.34480139, 0.3217531 , 0.33344551]),
  'dist_matrix': array([[1.        , 0.        , 0.5       , 0.        , 0.        ,
          0.        , 0.5       , 0.        , 0.        , 0.        ],
         [0.   

In [259]:
dist_list.index(min(dist_list))

4

In [260]:
dist_list.index(max(dist_list))

30

In [261]:
min(dist_list)

0.26150600000000024

In [262]:
max(dist_list)

0.6521730000000008

In [263]:
emd_trials[4]

{'distance': 0.26150600000000024,
 'flow_matrix': [[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.34719, 0.087593],
  [0.0, 0.0, 0.0, 0.0, 0.0, 0.108195, 0.0, 0.02224],
  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.173913],
  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.043478],
  [0.0, 0.0, 0.0, 0.0, 0.0, 0.217391, 0.0, 0.0],
  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0],
  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0],
  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]],
 'actual_bins': [['a'], ['b', 'c'], ['a', 'c'], ['a', 'b'], ['c']],
 'actual_freq_norm': array([0.43478261, 0.13043478, 0.17391304, 0.04347826, 0.2173913 ,
        0.        , 0.        , 0.        ]),
 'ext_bins': [['c'], ['a'], ['a', 'c']],
 'ext_freq_norm': array([0.        , 0.        , 0.        , 0.        , 0.        ,
        0.32558571, 0.34719023, 0.32722406]),
 'dist_matrix': array([[0., 2., 1., 1., 1., 1., 0., 1.],
        [2., 0., 1., 2., 1., 1., 2., 1.],
        [1., 1., 0., 1., 1., 1., 1., 0.],
        [1., 2., 1., 0., 2., 2., 1., 1.],
        

In [255]:
emd_trials[2]

{'distance': 0.6521740000000003,
 'flow_matrix': [[0.0, 0.0, 0.0, 0.0, 0.0, 0.222942, 0.211841, 0.0],
  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.130435],
  [0.0, 0.0, 0.0, 0.0, 0.0, 0.173913, 0.0, 0.0],
  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.043478, 0.0],
  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.073148, 0.144243],
  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0],
  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0],
  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]],
 'actual_bins': [['a'], ['b', 'c'], ['a', 'c'], ['b'], ['c']],
 'actual_freq_norm': array([0.43478261, 0.13043478, 0.17391304, 0.04347826, 0.2173913 ,
        0.        , 0.        , 0.        ]),
 'ext_bins': [['a', 'c'], ['b'], ['b', 'c']],
 'ext_freq_norm': array([0.        , 0.        , 0.        , 0.        , 0.        ,
        0.39685507, 0.32846688, 0.27467806]),
 'dist_matrix': array([[0., 2., 1., 1., 1., 1., 1., 2.],
        [2., 0., 1., 1., 1., 1., 1., 0.],
        [1., 1., 0., 2., 1., 0., 2., 1.],
        [1., 1., 2., 0., 1., 2., 0., 1.],
       

In [264]:
for i in range(8):
    for j in range(8):
        if emd_trials[4]['flow_matrix'][i][j] != 0.0:
            print(emd_trials[4]['flow_matrix'][i][j], (i,j))

0.34719 (0, 6)
0.087593 (0, 7)
0.108195 (1, 5)
0.02224 (1, 7)
0.173913 (2, 7)
0.043478 (3, 7)
0.217391 (4, 5)


In [265]:
print(emd_trials[4]['actual_bins'],'\n',
     emd_trials[4]['ext_bins'])

[['a'], ['b', 'c'], ['a', 'c'], ['a', 'b'], ['c']] 
 [['c'], ['a'], ['a', 'c']]


In [245]:
print(emd_trials[17]['actual_bins'],'\n',
     emd_trials[17]['ext_bins'])

[['a'], ['b', 'c'], ['a', 'c'], ['b'], ['c']] 
 [['b'], ['a'], ['c']]


In [246]:
for i in range(8):
    for j in range(8):
        if emd_trials[17]['flow_matrix'][i][j] != 0.0:
            print(emd_trials[17]['flow_matrix'][i][j], (i,j))

0.103891 (0, 5)
0.330892 (0, 7)
0.130435 (1, 6)
0.173913 (2, 5)
0.019446 (3, 6)
0.024032 (3, 7)
0.217391 (4, 6)


In [207]:
emd_trials[1]

{'distance': 1.1102230246251565e-16,
 'flow_matrix': [[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.338448, 0.096335],
  [0.0, 0.0, 0.0, 0.0, 0.0, 0.130434, 0.0, 0.0],
  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.173913],
  [0.0, 0.0, 0.0, 0.0, 0.0, 0.043478, 0.0, 0.0],
  [0.0, 0.0, 0.0, 0.0, 0.0, 0.127237, 0.0, 0.090154],
  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0],
  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0],
  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]],
 'actual_bins': [['a'], ['b', 'c'], ['a', 'c'], ['b'], ['c']],
 'actual_freq_norm': array([0.43478261, 0.13043478, 0.17391304, 0.04347826, 0.2173913 ,
        0.        , 0.        , 0.        ]),
 'ext_bins': [['a'], ['b', 'c'], ['b']],
 'ext_freq_norm': array([0.        , 0.        , 0.        , 0.        , 0.        ,
        0.30114945, 0.33844827, 0.36040228]),
 'dist_matrix': array([[1.        , 0.        , 0.5       , 0.        , 0.        ,
         1.        , 0.        , 0.        ],
        [0.        , 1.        , 0.33333333, 0.5       , 0.5 

In [12]:
bin_freq = {}
bin_labels['freq'] = 0
for i, val in path_df.iterrows():
    label_list = val['new_col'].split(',')
    for j, val2 in enumerate(label_list):
        bin_labels.loc[bin_labels['label'] == val2[1:-1], 'freq'] += 1

In [13]:
bin_labels.loc[bin_labels['freq']!=0,].shape

(72, 3)

In [14]:
bin_labels.head()

label     x  freq
0     A  0.65     0
1     B  1.60     3
2     C  2.70     2
3     D  2.95     6
4     E  4.65     5

In [15]:
bin_labels = bin_labels.sort_values(by=['x']).reset_index(drop=True)

In [16]:
bin_labels = bin_labels.loc[bin_labels['freq'] != 0].reset_index(drop=True) ## Try fixing at R level.

In [17]:
bin_labels

label     x  freq
0      B  1.60     3
1      I  1.65     1
2     CU  1.70     2
3     AW  1.75     2
4      R  1.85     1
5     CY  2.35     3
6     BZ  2.40     3
7     CI  2.45     3
8     AD  2.50     7
9     BE  2.55     2
10    AL  2.60     1
11     C  2.70     2
12    AY  2.75     4
13    BJ  2.80     1
14     N  2.85     2
15     S  2.90     2
16     D  2.95     6
17    BK  3.00     1
18     J  3.05     2
19     T  3.10     4
20    BU  3.15     3
21     Y  3.20     2
22     O  3.25     3
23    AS  3.30     4
24    AE  3.35     2
25    BO  3.40     2
26    BQ  3.45     2
27    DW  4.15     1
28    BX  4.25     1
29    CW  4.30     1
..   ...   ...   ...
42    CZ  5.00     4
43     U  5.05     5
44    CL  5.10     4
45     F  5.15     1
46    AZ  5.20     1
47    CD  5.25     4
48    BF  5.30     9
49     V  5.35     6
50    AM  5.40     1
51     K  5.45     7
52    AF  5.50     6
53     P  5.55     3
54    CS  5.60     4
55    AQ  5.65     1
56    CR  5.70     2
57    CX  5.75     7
58     G  5.80     7
59    CP  5.85     4
60    AG  5.90     4
61    AB  5.95     2
62    BL  6.00     2
63    BI  6.05     5
64    AX  6.10     2
65     L  6.15     3
66    AN  6.20     3
67    BV  6.25     1
68    DE  6.35     3
69    DI  6.70     1
70    CF  6.75     1
71    CO  6.80     1

[72 rows x 3 columns]

In [18]:
actual_bins = bin_labels['x'].tolist()

In [21]:
len(actual_bins)

72

In [24]:
import pyemd
import random
from sklearn.preprocessing import normalize
from scipy.spatial import distance as scipy_distance
from copy import copy
import numpy as np

dist_list = []
emd_trials = {}
for index in range(1000):
    ext_bins = sorted(np.random.uniform(actual_bins[0],actual_bins[-1], 5))
    ext_freq = []
    # actual_freq = [10.0, 3.0, 4.0, 1.0, 5.0]
    actual_freq = bin_labels['freq'].tolist()
    actual_freq_norm = normalize([actual_freq], norm='l1').reshape(72,)
    for i, x in enumerate(ext_bins):
        new_freq = []
        for j, b in enumerate(actual_bins):
            c = 1/(np.sqrt(2*np.pi))
            # dist = -(((x-b)**2)/2)
            dist = -((np.power((x-b),2))/2)
            d = np.exp(dist)
            w = c * d
            new_freq.append(w * actual_freq[j])
        ext_freq.append(sum(new_freq))

    combined_bins = copy(actual_bins)
    for _, val in enumerate(ext_bins):
        combined_bins.append(val)

    # dist_matrix = np.zeros((112,112), dtype='float64')
    dist_matrix = np.zeros((77,77), dtype='float64')
    ## Distance
    for i, val in enumerate(combined_bins):
        for j, val_2 in enumerate(combined_bins):
            dist_matrix[i,j] = scipy_distance.euclidean(combined_bins[i], combined_bins[j])
    
    ext_freq_norm = normalize([ext_freq], norm='l1').reshape(5,)
    
    for i in range(len(actual_freq)):
        # ext_freq.insert(0, 0.0)
        ext_freq_norm = np.insert(ext_freq_norm, 0, 0.0)

    for i in range(len(ext_bins)):
        # actual_freq.append(0.0)
        actual_freq_norm = np.append(actual_freq_norm, 0.0)

    # ext_freq = np.array(ext_freq)    
    # actual_freq = np.array(actual_freq)
    
    emd_val, min_cost_flow = pyemd.emd_with_flow(actual_freq_norm, ext_freq_norm, dist_matrix)
    dist_list.append(emd_val)
    emd_trials.update({index:{'distance':emd_val, 'flow_matrix':min_cost_flow,
                             'actual_bins':actual_bins, 'actual_freq_norm':actual_freq_norm,
                             'ext_bins':ext_bins, 'ext_freq_norm':ext_freq_norm,
                             'dist_matrix': dist_matrix}})

In [25]:
dist_list.index(min(dist_list))

845

In [80]:
bin_labels

label     x  freq  new_bins  new_index new_labels
0      B  1.60     3  2.566580          0          A
1      I  1.65     1  2.566580          0          A
2     CU  1.70     2  2.566580          0          A
3     AW  1.75     2  2.566580          0          A
4      R  1.85     1  2.566580          0          A
5     CY  2.35     3  2.566580          0          A
6     BZ  2.40     3  2.566580          0          A
7     CI  2.45     3  2.566580          0          A
8     AD  2.50     7  2.566580          0          A
9     BE  2.55     2  2.566580          0          A
10    AL  2.60     1  2.566580          0          A
11     C  2.70     2  2.566580          0          A
12    AY  2.75     4  3.235294          1          B
13    BJ  2.80     1  3.235294          1          B
14     N  2.85     2  3.235294          1          B
15     S  2.90     2  3.235294          1          B
16     D  2.95     6  3.235294          1          B
17    BK  3.00     1  3.235294          1          B
18     J  3.05     2  3.235294          1          B
19     T  3.10     4  3.235294          1          B
20    BU  3.15     3  3.235294          1          B
21     Y  3.20     2  3.235294          1          B
22     O  3.25     3  3.235294          1          B
23    AS  3.30     4  3.235294          1          B
24    AE  3.35     2  3.235294          1          B
25    BO  3.40     2  4.859467          2          C
26    BQ  3.45     2  4.859467          2          C
27    DW  4.15     1  4.859467          2          C
28    BX  4.25     1  4.859467          2          C
29    CW  4.30     1  4.859467          2          C
..   ...   ...   ...       ...        ...        ...
42    CZ  5.00     4  5.325707          3          D
43     U  5.05     5  5.325707          3          D
44    CL  5.10     4  5.325707          3          D
45     F  5.15     1  5.325707          3          D
46    AZ  5.20     1  5.325707          3          D
47    CD  5.25     4  5.325707          3          D
48    BF  5.30     9  5.325707          3          D
49     V  5.35     6  5.325707          3          D
50    AM  5.40     1  5.325707          3          D
51     K  5.45     7  5.325707          3          D
52    AF  5.50     6  5.325707          3          D
53     P  5.55     3  5.325707          3          D
54    CS  5.60     4  5.325707          3          D
55    AQ  5.65     1  5.325707          3          D
56    CR  5.70     2  5.325707          3          D
57    CX  5.75     7  5.325707          3          D
58     G  5.80     7  6.311841          4          E
59    CP  5.85     4  6.311841          4          E
60    AG  5.90     4  6.311841          4          E
61    AB  5.95     2  6.311841          4          E
62    BL  6.00     2  6.311841          4          E
63    BI  6.05     5  6.311841          4          E
64    AX  6.10     2  6.311841          4          E
65     L  6.15     3  6.311841          4          E
66    AN  6.20     3  6.311841          4          E
67    BV  6.25     1  6.311841          4          E
68    DE  6.35     3  6.311841          4          E
69    DI  6.70     1  6.311841          4          E
70    CF  6.75     1  6.311841          4          E
71    CO  6.80     1  6.311841          4          E

[72 rows x 6 columns]

In [79]:
emd_trials[845]['actual_bins']

[1.6,
 1.65,
 1.7,
 1.75,
 1.85,
 2.35,
 2.4,
 2.45,
 2.5,
 2.55,
 2.6,
 2.7,
 2.75,
 2.8,
 2.85,
 2.9,
 2.95,
 3.0,
 3.05,
 3.1,
 3.15,
 3.2,
 3.25,
 3.3,
 3.35,
 3.4,
 3.45,
 4.15,
 4.25,
 4.3,
 4.4,
 4.45,
 4.5,
 4.55,
 4.6,
 4.65,
 4.7,
 4.75,
 4.8,
 4.85,
 4.9,
 4.95,
 5.0,
 5.05,
 5.1,
 5.15,
 5.2,
 5.25,
 5.3,
 5.35,
 5.4,
 5.45,
 5.5,
 5.55,
 5.6,
 5.65,
 5.7,
 5.75,
 5.8,
 5.85,
 5.9,
 5.95,
 6.0,
 6.05,
 6.1,
 6.15,
 6.2,
 6.25,
 6.35,
 6.7,
 6.75,
 6.8]

In [26]:
min(dist_list)

0.2508107275024024

In [27]:
reduced_bins = emd_trials[845]['ext_bins']

In [28]:
len(reduced_bins)

5

In [29]:
np.array(emd_trials[845]['flow_matrix']).shape

(77, 77)

In [32]:
from dict_deep import deep_set
bin_mappings = get_bin_mappings(77, 845)

In [33]:
bin_mappings

{0: {72: 0.013097000000000006},
 1: {72: 0.004367000000000002},
 2: {72: 0.008734000000000004},
 3: {72: 0.008734000000000004},
 4: {72: 0.004367000000000002},
 5: {72: 0.013100000000000006},
 6: {72: 0.013100000000000006},
 7: {72: 0.013100000000000006},
 8: {72: 0.030568000000000015},
 9: {72: 0.008734000000000004},
 10: {72: 0.004367000000000002},
 11: {72: 0.0068100000000000036, 73: 0.0019240000000000008},
 12: {73: 0.017467000000000007},
 13: {73: 0.004367000000000002},
 14: {73: 0.008734000000000004},
 15: {73: 0.008734000000000004},
 16: {73: 0.026201000000000012},
 17: {73: 0.004367000000000002},
 18: {73: 0.008734000000000004},
 19: {73: 0.017467000000000007},
 20: {73: 0.013100000000000006},
 21: {73: 0.008734000000000004},
 22: {73: 0.013100000000000006},
 23: {73: 0.017467000000000007},
 24: {73: 0.0067120000000000036, 74: 0.002022000000000001},
 25: {74: 0.008734000000000004},
 26: {74: 0.008734000000000004},
 27: {74: 0.004367000000000002},
 28: {74: 0.004367000000000002}

In [34]:
from string import ascii_uppercase
labels = []
for i in range(len(ascii_uppercase)):
    labels.append(ascii_uppercase[i])
    
for i in range(len(ascii_uppercase)):
    if len(labels) >= 41:
        break
    for j in range(len(ascii_uppercase)):
        labels.append("".join([ascii_uppercase[i],ascii_uppercase[j]]))

In [35]:
len(labels)

52

In [36]:
bin_labels['new_bins'] = 0
bin_labels['new_index'] = 0
bin_labels['new_labels'] = ""

In [37]:
bin_labels.head()

label     x  freq  new_bins  new_index new_labels
0     B  1.60     3         0          0           
1     I  1.65     1         0          0           
2    CU  1.70     2         0          0           
3    AW  1.75     2         0          0           
4     R  1.85     1         0          0

In [38]:
len(reduced_bins)

5

In [39]:
import operator
for i, (k,val) in enumerate(bin_mappings.items()):
    reduced_bin_index = max(val.items(), key=operator.itemgetter(1))[0] - 72
    bin_labels.loc[k,'new_index'] = reduced_bin_index
    bin_labels.loc[k,'new_bins'] = reduced_bins[reduced_bin_index]
    bin_labels.loc[k,'new_labels'] = labels[reduced_bin_index]

In [40]:
bin_labels

label     x  freq  new_bins  new_index new_labels
0      B  1.60     3  2.566580          0          A
1      I  1.65     1  2.566580          0          A
2     CU  1.70     2  2.566580          0          A
3     AW  1.75     2  2.566580          0          A
4      R  1.85     1  2.566580          0          A
5     CY  2.35     3  2.566580          0          A
6     BZ  2.40     3  2.566580          0          A
7     CI  2.45     3  2.566580          0          A
8     AD  2.50     7  2.566580          0          A
9     BE  2.55     2  2.566580          0          A
10    AL  2.60     1  2.566580          0          A
11     C  2.70     2  2.566580          0          A
12    AY  2.75     4  3.235294          1          B
13    BJ  2.80     1  3.235294          1          B
14     N  2.85     2  3.235294          1          B
15     S  2.90     2  3.235294          1          B
16     D  2.95     6  3.235294          1          B
17    BK  3.00     1  3.235294          1          B
18     J  3.05     2  3.235294          1          B
19     T  3.10     4  3.235294          1          B
20    BU  3.15     3  3.235294          1          B
21     Y  3.20     2  3.235294          1          B
22     O  3.25     3  3.235294          1          B
23    AS  3.30     4  3.235294          1          B
24    AE  3.35     2  3.235294          1          B
25    BO  3.40     2  4.859467          2          C
26    BQ  3.45     2  4.859467          2          C
27    DW  4.15     1  4.859467          2          C
28    BX  4.25     1  4.859467          2          C
29    CW  4.30     1  4.859467          2          C
..   ...   ...   ...       ...        ...        ...
42    CZ  5.00     4  5.325707          3          D
43     U  5.05     5  5.325707          3          D
44    CL  5.10     4  5.325707          3          D
45     F  5.15     1  5.325707          3          D
46    AZ  5.20     1  5.325707          3          D
47    CD  5.25     4  5.325707          3          D
48    BF  5.30     9  5.325707          3          D
49     V  5.35     6  5.325707          3          D
50    AM  5.40     1  5.325707          3          D
51     K  5.45     7  5.325707          3          D
52    AF  5.50     6  5.325707          3          D
53     P  5.55     3  5.325707          3          D
54    CS  5.60     4  5.325707          3          D
55    AQ  5.65     1  5.325707          3          D
56    CR  5.70     2  5.325707          3          D
57    CX  5.75     7  5.325707          3          D
58     G  5.80     7  6.311841          4          E
59    CP  5.85     4  6.311841          4          E
60    AG  5.90     4  6.311841          4          E
61    AB  5.95     2  6.311841          4          E
62    BL  6.00     2  6.311841          4          E
63    BI  6.05     5  6.311841          4          E
64    AX  6.10     2  6.311841          4          E
65     L  6.15     3  6.311841          4          E
66    AN  6.20     3  6.311841          4          E
67    BV  6.25     1  6.311841          4          E
68    DE  6.35     3  6.311841          4          E
69    DI  6.70     1  6.311841          4          E
70    CF  6.75     1  6.311841          4          E
71    CO  6.80     1  6.311841          4          E

[72 rows x 6 columns]

##### Updated paths 

In [41]:
path_df.head()

new_col
0  1G0,2D1
1  3E0,1K0
2      1P0
3      3C0
4  3Z0,1K0

In [42]:
path_df['updated_path'] = ""

In [43]:
path_df.head()

new_col updated_path
0  1G0,2D1             
1  3E0,1K0             
2      1P0             
3      3C0             
4  3Z0,1K0

In [44]:
bin_labels.head()

label     x  freq  new_bins  new_index new_labels
0     B  1.60     3   2.56658          0          A
1     I  1.65     1   2.56658          0          A
2    CU  1.70     2   2.56658          0          A
3    AW  1.75     2   2.56658          0          A
4     R  1.85     1   2.56658          0          A

In [45]:
for i, val in path_df.iterrows():
    label_list = val['new_col'].split(',')
    updated_list = []
    for j, val2 in enumerate(label_list):
        # bin_labels.loc[bin_labels['label'] == val2[1:-1], 'freq'] += 1
        new_label = bin_labels.loc[bin_labels['label'] == val2[1:-1]]['new_labels'].values[0]
        updated_list.append(val2[0] + new_label + val2[-1])
        if len(updated_list)>1:
            path_df.loc[i,'updated_path'] = (',').join(updated_list)
        else:
            path_df.loc[i,'updated_path'] = updated_list[0]
        

In [46]:
path_df

new_col updated_path
0      1G0,2D1      1E0,2B1
1      3E0,1K0      3C0,1D0
2          1P0          1D0
3          3C0          3A0
4      3Z0,1K0      3C0,1D0
5         2AE1          2B1
6          2J1          2B1
7         3AL0          3A0
8          3C0          3A0
9         1AG0          1E0
10        1AF0          1D0
11         2T1          2B1
12        3AY0          3B0
13        3AD0          3A0
14   3BH0,2AS1      3C0,2B1
15   3AI0,2AS1      3C0,2B1
16        1AF0          1D0
17    2D1,1AG0      2B1,1E0
18   4AW0,2BQ1      4A0,2C1
19        1BF0          1D0
20    1AB0,1K0      1E0,1D0
21        3AD0          3A0
22        3AY0          3B0
23    3BX0,1V0      3C0,1D0
24        3BU0          3B0
25         3N0          3B0
26   1CF0,1AF0      1E0,1D0
27         3T0          3B0
28        3AD0          3A0
29   2BK1,1BI0      2B1,1E0
..         ...          ...
120       3AJ1          3C1
121       3DR1          3C1
122        1G1          1E1
123  3BZ1,1BL1      3A1,1E1
124       3BH1          3C1
125       1CX1          1D1
126   3S1,1AG1      3B1,1E1
127       3BM1          3C1
128       1AN1          1E1
129       1AB1          1E1
130        3Z1          3C1
131       3AI1          3C1
132    1V1,3U1      1D1,3D1
133       1BL1          1E1
134       1AF1          1D1
135       3CZ1          3D1
136       3CN1          3C1
137       3AI1          3C1
138       3CQ1          3C1
139       3AP1          3C1
140  1CX1,3AP1      1D1,3C1
141  1CP1,3CN1      1E1,3C1
142       1CX1          1D1
143        1K1          1D1
144  1CX1,3AI1      1D1,3C1
145       3AP1          3C1
146       3AJ1          3C1
147       1BI1          1E1
148   2S1,1CR1      2B1,1D1
149       3AI1          3C1

[150 rows x 2 columns]

In [47]:
bin_labels.head()

label     x  freq  new_bins  new_index new_labels
0     B  1.60     3   2.56658          0          A
1     I  1.65     1   2.56658          0          A
2    CU  1.70     2   2.56658          0          A
3    AW  1.75     2   2.56658          0          A
4     R  1.85     1   2.56658          0          A

In [48]:
test_data.head()

0         1         2         3  new_col
0 -0.900681  1.019004 -1.340227 -1.315444  1G0,2D1
1 -1.143017 -0.131979 -1.340227 -1.315444  3E0,1K0
2 -1.385353  0.328414 -1.397064 -1.315444      1P0
3 -1.506521  0.098217 -1.283389 -1.315444      3C0
4 -1.021849  1.249201 -1.340227 -1.315444  3Z0,1K0

In [49]:
path_df.head()

new_col updated_path
0  1G0,2D1      1E0,2B1
1  3E0,1K0      3C0,1D0
2      1P0          1D0
3      3C0          3A0
4  3Z0,1K0      3C0,1D0

In [52]:
test_data = test_data.drop(["new_col"], axis=1)
# test_data = test_data.drop(["updated_path"], axis=1)

In [53]:
test_data.head()

0         1         2         3
0 -0.900681  1.019004 -1.340227 -1.315444
1 -1.143017 -0.131979 -1.340227 -1.315444
2 -1.385353  0.328414 -1.397064 -1.315444
3 -1.506521  0.098217 -1.283389 -1.315444
4 -1.021849  1.249201 -1.340227 -1.315444

In [54]:
### Move to bottom trials

test_data = pd.concat([test_data, path_df.loc[:,'updated_path']], axis=1)
updated_path = []
for i, val in test_data.iterrows():
    updated_path.append(val['updated_path'].split(sep=","))

_ = [x.insert(0, 'S') for x in updated_path]
_ = [x.append('E') for x in updated_path]

test_data['updated_path'] = updated_path

# test_data = test_data.drop(["updated_path"], axis=1)

paths_lengths = np.array([len(xi) for xi in test_data.iloc[:,-1]])

label_char = []
for _, i in enumerate(np.unique(test_data['updated_path'])):
    for _, j in enumerate(i):
        if j not in label_char:
            label_char.append(j)

label_indices = { j : i for i, j in enumerate(label_char) }
indices_label = { i : j for i, j in enumerate(label_char) }

input_path_sequence = []
next_chars = []
features = []
paths_maxlen = np.max(paths_lengths)
# path_vocab_size = len(bin_labels) # How is this working? Validate!
path_vocab_size = len(indices_label) # Temporary test for local trees
feature_size = 4
for i in range(0, len(test_data)):
    # get the feature
    curr_feat = np.array([test_data.iloc[i, 0:4]])
    curr_path = test_data.iloc[i, -1]
    curr_path_len = len(curr_path)
    # curr_label = y[i]
    # curr_dec_feat = df.iloc[i, 6]
    for j in range(1, curr_path_len):
        features.append(curr_feat)
        input_path_sequence.append(curr_path[0:j])
        next_chars.append(curr_path[j])

## Vectorize inputs        

x_path = np.zeros(
    (len(input_path_sequence), paths_maxlen, path_vocab_size), dtype=np.bool)

path_latent_input = np.zeros(
    (len(input_path_sequence), feature_size), dtype=np.float)

y_path = np.zeros(
    (len(input_path_sequence), path_vocab_size), dtype=np.bool)

# print(input_path_sequence)
# print(len(input_path_sequence))
for i, sentence in enumerate(input_path_sequence):
    for t, char in enumerate(sentence):
        # x_path[i, t, self.char_indices[char]] = 1
        # print(bin_labels.index[bin_labels['label'] == char[1]])
        # index = bin_labels.index[bin_labels['label'] == char[1]].tolist()[0]
        x_path[i, t, label_indices[char]] = 1
    # y_path[i, char_indices[next_chars[i]]] = 1
    # index = bin_labels.index[bin_labels['label'] == next_chars[i][1]].tolist()[0]
    # y_path[i, index] = 1
    y_path[i, label_indices[next_chars[i]]] = 1
    path_latent_input[i, :] = features[i]

##### Trials with bins reduced to 70 to 40
- label indices reduced from 117 to 89


In [235]:
combined_model_trial_2 = _create_combined_model()
label_model_trial_2 = _create_label_model()

def fit_model():

    y_cat = to_categorical(y)

    label_model_trial_2.compile(
        optimizer='adam', loss='categorical_crossentropy', metrics=['accuracy'])
    label_model_trial_2.fit(
        X, y_cat, batch_size=30, epochs=150, verbose=1, shuffle=True, validation_split=0.2)

    x_latent = get_hidden_x(path_latent_input, model=label_model_trial_2)

    combined_model_trial_2.compile(
        optimizer='adam', loss='categorical_crossentropy', metrics=['accuracy'])
    combined_model_trial_2.fit([x_latent, x_path], y_path,
                           batch_size=30, epochs=1000, verbose=1, shuffle=True)

In [237]:
x_path.shape

(379, 5, 89)

In [238]:
y_path.shape

(379, 89)

In [236]:
fit_model()

Train on 120 samples, validate on 30 samples
Epoch 1/150
120/120 [==============================] - 0s 3ms/step - loss: 1.1343 - acc: 0.3250 - val_loss: 1.1757 - val_acc: 0.4000
Epoch 2/150
120/120 [==============================] - 0s 43us/step - loss: 1.0254 - acc: 0.5000 - val_loss: 1.1400 - val_acc: 0.3667
Epoch 3/150
120/120 [==============================] - 0s 40us/step - loss: 0.9267 - acc: 0.6250 - val_loss: 1.1125 - val_acc: 0.2000
Epoch 4/150
120/120 [==============================] - 0s 37us/step - loss: 0.8458 - acc: 0.6333 - val_loss: 1.0942 - val_acc: 0.1000
Epoch 5/150
120/120 [==============================] - 0s 38us/step - loss: 0.7771 - acc: 0.6750 - val_loss: 1.0818 - val_acc: 0.0667
Epoch 6/150
120/120 [==============================] - 0s 42us/step - loss: 0.7206 - acc: 0.7583 - val_loss: 1.0737 - val_acc: 0.0667
Epoch 7/150
120/120 [==============================] - 0s 81us/step - loss: 0.6741 - acc: 0.7833 - val_loss: 1.0683 - val_acc: 0.0333
Epoch 8/150
120/12

120/120 [==============================] - 0s 45us/step - loss: 0.2090 - acc: 0.9750 - val_loss: 0.5243 - val_acc: 0.9000
Epoch 62/150
120/120 [==============================] - 0s 35us/step - loss: 0.2047 - acc: 0.9750 - val_loss: 0.5104 - val_acc: 0.9000
Epoch 63/150
120/120 [==============================] - 0s 62us/step - loss: 0.2001 - acc: 0.9750 - val_loss: 0.5068 - val_acc: 0.9000
Epoch 64/150
120/120 [==============================] - 0s 41us/step - loss: 0.1962 - acc: 0.9750 - val_loss: 0.5084 - val_acc: 0.9000
Epoch 65/150
120/120 [==============================] - 0s 32us/step - loss: 0.1921 - acc: 0.9750 - val_loss: 0.5021 - val_acc: 0.9000
Epoch 66/150
120/120 [==============================] - 0s 47us/step - loss: 0.1881 - acc: 0.9750 - val_loss: 0.4996 - val_acc: 0.9000
Epoch 67/150
120/120 [==============================] - 0s 44us/step - loss: 0.1842 - acc: 0.9750 - val_loss: 0.4994 - val_acc: 0.9000
Epoch 68/150
120/120 [==============================] - 0s 58us/step

120/120 [==============================] - 0s 54us/step - loss: 0.0700 - acc: 0.9917 - val_loss: 0.3733 - val_acc: 0.9000
Epoch 122/150
120/120 [==============================] - 0s 46us/step - loss: 0.0690 - acc: 0.9917 - val_loss: 0.3776 - val_acc: 0.9000
Epoch 123/150
120/120 [==============================] - 0s 36us/step - loss: 0.0679 - acc: 0.9917 - val_loss: 0.3854 - val_acc: 0.9000
Epoch 124/150
120/120 [==============================] - 0s 45us/step - loss: 0.0670 - acc: 0.9917 - val_loss: 0.3920 - val_acc: 0.9000
Epoch 125/150
120/120 [==============================] - 0s 38us/step - loss: 0.0663 - acc: 0.9917 - val_loss: 0.3935 - val_acc: 0.9000
Epoch 126/150
120/120 [==============================] - 0s 46us/step - loss: 0.0653 - acc: 0.9917 - val_loss: 0.3927 - val_acc: 0.9000
Epoch 127/150
120/120 [==============================] - 0s 42us/step - loss: 0.0645 - acc: 0.9917 - val_loss: 0.3920 - val_acc: 0.9000
Epoch 128/150
120/120 [==============================] - 0s 63

379/379 [==============================] - 0s 116us/step - loss: 3.0070 - acc: 0.3958
Epoch 43/1000
379/379 [==============================] - 0s 91us/step - loss: 3.0023 - acc: 0.3958
Epoch 44/1000
379/379 [==============================] - 0s 133us/step - loss: 2.9976 - acc: 0.3958
Epoch 45/1000
379/379 [==============================] - 0s 115us/step - loss: 2.9928 - acc: 0.3958
Epoch 46/1000
379/379 [==============================] - 0s 113us/step - loss: 2.9883 - acc: 0.3958
Epoch 47/1000
379/379 [==============================] - 0s 135us/step - loss: 2.9841 - acc: 0.3958
Epoch 48/1000
379/379 [==============================] - 0s 118us/step - loss: 2.9796 - acc: 0.3958
Epoch 49/1000
379/379 [==============================] - 0s 127us/step - loss: 2.9754 - acc: 0.3958
Epoch 50/1000
379/379 [==============================] - 0s 124us/step - loss: 2.9709 - acc: 0.3958
Epoch 51/1000
379/379 [==============================] - 0s 109us/step - loss: 2.9666 - acc: 0.3958
Epoch 52/1000
3

379/379 [==============================] - 0s 112us/step - loss: 2.3622 - acc: 0.4169
Epoch 124/1000
379/379 [==============================] - 0s 117us/step - loss: 2.3560 - acc: 0.4169
Epoch 125/1000
379/379 [==============================] - 0s 111us/step - loss: 2.3514 - acc: 0.4169
Epoch 126/1000
379/379 [==============================] - 0s 116us/step - loss: 2.3479 - acc: 0.4222
Epoch 127/1000
379/379 [==============================] - 0s 108us/step - loss: 2.3423 - acc: 0.4195
Epoch 128/1000
379/379 [==============================] - 0s 126us/step - loss: 2.3382 - acc: 0.4222
Epoch 129/1000
379/379 [==============================] - 0s 127us/step - loss: 2.3340 - acc: 0.4195
Epoch 130/1000
379/379 [==============================] - 0s 105us/step - loss: 2.3296 - acc: 0.4222
Epoch 131/1000
379/379 [==============================] - 0s 131us/step - loss: 2.3241 - acc: 0.4195
Epoch 132/1000
379/379 [==============================] - 0s 108us/step - loss: 2.3224 - acc: 0.4222
Epoch

...

379/379 [==============================] - 0s 102us/step - loss: 1.8111 - acc: 0.4960
Epoch 610/1000
379/379 [==============================] - 0s 93us/step - loss: 1.8105 - acc: 0.4987
Epoch 611/1000
379/379 [==============================] - 0s 109us/step - loss: 1.8096 - acc: 0.4960
Epoch 612/1000
379/379 [==============================] - 0s 103us/step - loss: 1.8092 - acc: 0.4908
Epoch 613/1000
379/379 [==============================] - 0s 100us/step - loss: 1.8085 - acc: 0.4934
Epoch 614/1000
379/379 [==============================] - 0s 96us/step - loss: 1.8083 - acc: 0.5013
Epoch 615/1000
379/379 [==============================] - 0s 106us/step - loss: 1.8095 - acc: 0.5013
Epoch 616/1000
379/379 [==============================] - 0s 104us/step - loss: 1.8102 - acc: 0.4960
Epoch 617/1000
379/379 [==============================] - 0s 108us/step - loss: 1.8090 - acc: 0.4987
Epoch 618/1000
379/379 [==============================] - 0s 91us/step - loss: 1.8095 - acc: 0.4987
Epoch 61

379/379 [==============================] - 0s 104us/step - loss: 1.7753 - acc: 0.5013
Epoch 691/1000
379/379 [==============================] - 0s 110us/step - loss: 1.7743 - acc: 0.5066
Epoch 692/1000
379/379 [==============================] - 0s 107us/step - loss: 1.7740 - acc: 0.5066
Epoch 693/1000
379/379 [==============================] - 0s 118us/step - loss: 1.7744 - acc: 0.5066
Epoch 694/1000
379/379 [==============================] - 0s 109us/step - loss: 1.7724 - acc: 0.5066
Epoch 695/1000
379/379 [==============================] - 0s 105us/step - loss: 1.7743 - acc: 0.5040
Epoch 696/1000
379/379 [==============================] - 0s 106us/step - loss: 1.7736 - acc: 0.5066
Epoch 697/1000
379/379 [==============================] - 0s 106us/step - loss: 1.7730 - acc: 0.5066
Epoch 698/1000
379/379 [==============================] - 0s 112us/step - loss: 1.7719 - acc: 0.5119
Epoch 699/1000
379/379 [==============================] - 0s 112us/step - loss: 1.7704 - acc: 0.5066
Epoch

Epoch 771/1000
379/379 [==============================] - 0s 103us/step - loss: 1.7405 - acc: 0.5172
Epoch 772/1000
379/379 [==============================] - 0s 117us/step - loss: 1.7426 - acc: 0.5145
Epoch 773/1000
379/379 [==============================] - 0s 103us/step - loss: 1.7400 - acc: 0.5145
Epoch 774/1000
379/379 [==============================] - 0s 107us/step - loss: 1.7414 - acc: 0.5145
Epoch 775/1000
379/379 [==============================] - 0s 103us/step - loss: 1.7388 - acc: 0.5172
Epoch 776/1000
379/379 [==============================] - 0s 109us/step - loss: 1.7388 - acc: 0.5172
Epoch 777/1000
379/379 [==============================] - 0s 98us/step - loss: 1.7378 - acc: 0.5172
Epoch 778/1000
379/379 [==============================] - 0s 105us/step - loss: 1.7377 - acc: 0.5172
Epoch 779/1000
379/379 [==============================] - 0s 120us/step - loss: 1.7372 - acc: 0.5172
Epoch 780/1000
379/379 [==============================] - 0s 122us/step - loss: 1.7369 - acc

379/379 [==============================] - 0s 101us/step - loss: 1.7113 - acc: 0.5277
Epoch 853/1000
379/379 [==============================] - 0s 123us/step - loss: 1.7115 - acc: 0.5224
Epoch 854/1000
379/379 [==============================] - 0s 108us/step - loss: 1.7108 - acc: 0.5224
Epoch 855/1000
379/379 [==============================] - 0s 98us/step - loss: 1.7135 - acc: 0.5198
Epoch 856/1000
379/379 [==============================] - 0s 101us/step - loss: 1.7087 - acc: 0.5277
Epoch 857/1000
379/379 [==============================] - 0s 103us/step - loss: 1.7084 - acc: 0.5251
Epoch 858/1000
379/379 [==============================] - 0s 126us/step - loss: 1.7078 - acc: 0.5277
Epoch 859/1000
379/379 [==============================] - 0s 114us/step - loss: 1.7071 - acc: 0.5224
Epoch 860/1000
379/379 [==============================] - 0s 114us/step - loss: 1.7064 - acc: 0.5251
Epoch 861/1000
379/379 [==============================] - 0s 100us/step - loss: 1.7061 - acc: 0.5251
Epoch 

379/379 [==============================] - 0s 112us/step - loss: 1.6844 - acc: 0.5251
Epoch 934/1000
379/379 [==============================] - 0s 105us/step - loss: 1.6859 - acc: 0.5172
Epoch 935/1000
379/379 [==============================] - 0s 102us/step - loss: 1.6859 - acc: 0.5224
Epoch 936/1000
379/379 [==============================] - 0s 106us/step - loss: 1.6840 - acc: 0.5198
Epoch 937/1000
379/379 [==============================] - 0s 96us/step - loss: 1.6822 - acc: 0.5224
Epoch 938/1000
379/379 [==============================] - 0s 100us/step - loss: 1.6812 - acc: 0.5224
Epoch 939/1000
379/379 [==============================] - 0s 103us/step - loss: 1.6828 - acc: 0.5198
Epoch 940/1000
379/379 [==============================] - 0s 118us/step - loss: 1.6812 - acc: 0.5251
Epoch 941/1000
379/379 [==============================] - 0s 99us/step - loss: 1.6800 - acc: 0.5277
Epoch 942/1000
379/379 [==============================] - 0s 119us/step - loss: 1.6790 - acc: 0.5251
Epoch 9

In [319]:
combined_model_trial_2.summary()

__________________________________________________________________________________________________
Layer (type)                    Output Shape         Param #     Connected to                     
label_ip (InputLayer)           (None, 5)            0                                            
__________________________________________________________________________________________________
dec_feat_ip (InputLayer)        (None, 5, 89)        0                                            
__________________________________________________________________________________________________
gru_seq (GRU)                   (None, 5)            1425        dec_feat_ip[0][0]                
                                                                 label_ip[0][0]                   
__________________________________________________________________________________________________
cat (Concatenate)               (None, 10)           0           label_ip[0][0]                   
          

##### Bins reduced from 70 to 20

In [274]:
label_indices

{'S': 0,
 '1N1': 1,
 '3N0': 2,
 'E': 3,
 '1O0': 4,
 '1O1': 5,
 '1T0': 6,
 '3K1': 7,
 '1P0': 8,
 '1P1': 9,
 '3K0': 10,
 '3M0': 11,
 '3N1': 12,
 '4B0': 13,
 '1Q0': 14,
 '1Q1': 15,
 '1T1': 16,
 '3L1': 17,
 '4B1': 18,
 '1R0': 19,
 '2F1': 20,
 '1R1': 21,
 '3M1': 22,
 '1S0': 23,
 '2F0': 24,
 '1S1': 25,
 '2G0': 26,
 '2G1': 27,
 '2H0': 28,
 '2H1': 29,
 '2I0': 30,
 '2D1': 31,
 '4A0': 32,
 '2I1': 33,
 '2J0': 34,
 '3C0': 35,
 '3C1': 36,
 '3D0': 37,
 '3D1': 38,
 '3E0': 39,
 '3E1': 40,
 '3F0': 41,
 '3G1': 42,
 '3H0': 43,
 '3I0': 44,
 '3J0': 45,
 '1M1': 46,
 '3J1': 47,
 '3L0': 48,
 '1M0': 49,
 '3O0': 50,
 '3P0': 51,
 '4A1': 52,
 '2J1': 53}

In [283]:
path_df

new_col updated_path
0      1G0,2D1      1R0,2F1
1      3E0,1K0      3K0,1O0
2          1P0          1Q0
3          3C0          3F0
4      3Z0,1K0      3K0,1O0
5         2AE1          2I1
6          2J1          2G1
7         3AL0          3E0
8          3C0          3F0
9         1AG0          1S0
10        1AF0          1P0
11         2T1          2H1
12        3AY0          3E0
13        3AD0          3D0
14   3BH0,2AS1      3K0,2I1
15   3AI0,2AS1      3L0,2I1
16        1AF0          1P0
17    2D1,1AG0      2F1,1S0
18   4AW0,2BQ1      4B0,2J1
19        1BF0          1O0
20    1AB0,1K0      1S0,1O0
21        3AD0          3D0
22        3AY0          3E0
23    3BX0,1V0      3J0,1P0
24        3BU0          3H0
25         3N0          3F0
26   1CF0,1AF0      1T0,1P0
27         3T0          3H0
28        3AD0          3D0
29   2BK1,1BI0      2F1,1S0
..         ...          ...
120       3AJ1          3M1
121       3DR1          3J1
122        1G1          1R1
123  3BZ1,1BL1      3C1,1S1
124       3BH1          3K1
125       1CX1          1R1
126   3S1,1AG1      3G1,1S1
127       3BM1          3J1
128       1AN1          1T1
129       1AB1          1S1
130        3Z1          3K1
131       3AI1          3L1
132    1V1,3U1      1P1,3N1
133       1BL1          1S1
134       1AF1          1P1
135       3CZ1          3N1
136       3CN1          3L1
137       3AI1          3L1
138       3CQ1          3J1
139       3AP1          3M1
140  1CX1,3AP1      1R1,3M1
141  1CP1,3CN1      1Q1,3L1
142       1CX1          1R1
143        1K1          1O1
144  1CX1,3AI1      1R1,3L1
145       3AP1          3M1
146       3AJ1          3M1
147       1BI1          1S1
148   2S1,1CR1      2G1,1Q1
149       3AI1          3L1

[150 rows x 2 columns]

In [279]:
combined_model_trial_3 = _create_combined_model()
label_model_trial_3 = _create_label_model()

def fit_model():

    y_cat = to_categorical(y)

    label_model_trial_3.compile(
        optimizer='adam', loss='categorical_crossentropy', metrics=['accuracy'])
    label_model_trial_3.fit(
        X, y_cat, batch_size=30, epochs=150, verbose=1, shuffle=True, validation_split=0.2)

    x_latent = get_hidden_x(path_latent_input, model=label_model_trial_3)

    combined_model_trial_3.compile(
        optimizer='adam', loss='categorical_crossentropy', metrics=['accuracy'])
    combined_model_trial_3.fit([x_latent, x_path], y_path,
                           batch_size=30, epochs=1000, verbose=1, shuffle=True)

In [318]:
combined_model_trial_3.summary()

__________________________________________________________________________________________________
Layer (type)                    Output Shape         Param #     Connected to                     
label_ip (InputLayer)           (None, 5)            0                                            
__________________________________________________________________________________________________
dec_feat_ip (InputLayer)        (None, 5, 54)        0                                            
__________________________________________________________________________________________________
gru_seq (GRU)                   (None, 5)            900         dec_feat_ip[0][0]                
                                                                 label_ip[0][0]                   
__________________________________________________________________________________________________
cat (Concatenate)               (None, 10)           0           label_ip[0][0]                   
          

In [282]:
paths_maxlen

5

In [275]:
x_path.shape

(379, 5, 54)

In [276]:
y_path.shape

(379, 54)

In [278]:
len(input_path_sequence)

379

In [280]:
fit_model()

Train on 120 samples, validate on 30 samples
Epoch 1/150
120/120 [==============================] - 1s 5ms/step - loss: 1.4385 - acc: 0.1083 - val_loss: 1.2760 - val_acc: 0.0000e+00
Epoch 2/150
120/120 [==============================] - 0s 54us/step - loss: 1.3011 - acc: 0.2333 - val_loss: 1.1481 - val_acc: 0.1000
Epoch 3/150
120/120 [==============================] - 0s 51us/step - loss: 1.1929 - acc: 0.3417 - val_loss: 1.0400 - val_acc: 0.4333
Epoch 4/150
120/120 [==============================] - 0s 74us/step - loss: 1.0993 - acc: 0.4417 - val_loss: 0.9510 - val_acc: 0.7333
Epoch 5/150
120/120 [==============================] - 0s 76us/step - loss: 1.0241 - acc: 0.5167 - val_loss: 0.8772 - val_acc: 0.9000
Epoch 6/150
120/120 [==============================] - 0s 59us/step - loss: 0.9549 - acc: 0.5750 - val_loss: 0.8164 - val_acc: 0.9667
Epoch 7/150
120/120 [==============================] - 0s 104us/step - loss: 0.8953 - acc: 0.5833 - val_loss: 0.7686 - val_acc: 1.0000
Epoch 8/150
1

120/120 [==============================] - 0s 51us/step - loss: 0.1729 - acc: 0.9833 - val_loss: 0.3868 - val_acc: 0.9000
Epoch 62/150
120/120 [==============================] - 0s 42us/step - loss: 0.1701 - acc: 0.9833 - val_loss: 0.3879 - val_acc: 0.9000
Epoch 63/150
120/120 [==============================] - 0s 76us/step - loss: 0.1670 - acc: 0.9833 - val_loss: 0.3826 - val_acc: 0.9000
Epoch 64/150
120/120 [==============================] - 0s 43us/step - loss: 0.1647 - acc: 0.9833 - val_loss: 0.3737 - val_acc: 0.9000
Epoch 65/150
120/120 [==============================] - 0s 46us/step - loss: 0.1618 - acc: 0.9833 - val_loss: 0.3729 - val_acc: 0.9000
Epoch 66/150
120/120 [==============================] - 0s 32us/step - loss: 0.1591 - acc: 0.9833 - val_loss: 0.3722 - val_acc: 0.9000
Epoch 67/150
120/120 [==============================] - 0s 35us/step - loss: 0.1566 - acc: 0.9833 - val_loss: 0.3741 - val_acc: 0.9000
Epoch 68/150
120/120 [==============================] - 0s 44us/step

120/120 [==============================] - 0s 42us/step - loss: 0.0816 - acc: 0.9917 - val_loss: 0.3289 - val_acc: 0.8667
Epoch 122/150
120/120 [==============================] - 0s 45us/step - loss: 0.0806 - acc: 0.9917 - val_loss: 0.3260 - val_acc: 0.8667
Epoch 123/150
120/120 [==============================] - 0s 45us/step - loss: 0.0798 - acc: 0.9917 - val_loss: 0.3298 - val_acc: 0.8667
Epoch 124/150
120/120 [==============================] - 0s 54us/step - loss: 0.0790 - acc: 0.9917 - val_loss: 0.3301 - val_acc: 0.8667
Epoch 125/150
120/120 [==============================] - 0s 38us/step - loss: 0.0785 - acc: 0.9917 - val_loss: 0.3247 - val_acc: 0.8667
Epoch 126/150
120/120 [==============================] - 0s 50us/step - loss: 0.0776 - acc: 0.9917 - val_loss: 0.3295 - val_acc: 0.8667
Epoch 127/150
120/120 [==============================] - 0s 52us/step - loss: 0.0768 - acc: 0.9917 - val_loss: 0.3319 - val_acc: 0.8667
Epoch 128/150
120/120 [==============================] - 0s 42

379/379 [==============================] - 0s 121us/step - loss: 2.6393 - acc: 0.3958
Epoch 43/1000
379/379 [==============================] - 0s 135us/step - loss: 2.6332 - acc: 0.3958
Epoch 44/1000
379/379 [==============================] - 0s 139us/step - loss: 2.6268 - acc: 0.3958
Epoch 45/1000
379/379 [==============================] - 0s 144us/step - loss: 2.6207 - acc: 0.3958
Epoch 46/1000
379/379 [==============================] - 0s 133us/step - loss: 2.6147 - acc: 0.3958
Epoch 47/1000
379/379 [==============================] - 0s 115us/step - loss: 2.6090 - acc: 0.3958
Epoch 48/1000
379/379 [==============================] - 0s 133us/step - loss: 2.6025 - acc: 0.3958
Epoch 49/1000
379/379 [==============================] - 0s 129us/step - loss: 2.5966 - acc: 0.3958
Epoch 50/1000
379/379 [==============================] - 0s 148us/step - loss: 2.5905 - acc: 0.3958
Epoch 51/1000
379/379 [==============================] - 0s 156us/step - loss: 2.5842 - acc: 0.3958
Epoch 52/1000


379/379 [==============================] - 0s 141us/step - loss: 2.1433 - acc: 0.4301
Epoch 124/1000
379/379 [==============================] - 0s 131us/step - loss: 2.1402 - acc: 0.4380
Epoch 125/1000
379/379 [==============================] - 0s 143us/step - loss: 2.1380 - acc: 0.4354
Epoch 126/1000
379/379 [==============================] - 0s 140us/step - loss: 2.1354 - acc: 0.4301
Epoch 127/1000
379/379 [==============================] - 0s 107us/step - loss: 2.1327 - acc: 0.4354
Epoch 128/1000
379/379 [==============================] - 0s 135us/step - loss: 2.1302 - acc: 0.4354
Epoch 129/1000
379/379 [==============================] - 0s 122us/step - loss: 2.1280 - acc: 0.4354
Epoch 130/1000
379/379 [==============================] - 0s 126us/step - loss: 2.1259 - acc: 0.4380
Epoch 131/1000
379/379 [==============================] - 0s 120us/step - loss: 2.1234 - acc: 0.4406
Epoch 132/1000
379/379 [==============================] - 0s 130us/step - loss: 2.1207 - acc: 0.4301
Epoch

...

379/379 [==============================] - 0s 127us/step - loss: 1.7748 - acc: 0.4749
Epoch 610/1000
379/379 [==============================] - 0s 114us/step - loss: 1.7750 - acc: 0.4723
Epoch 611/1000
379/379 [==============================] - 0s 127us/step - loss: 1.7730 - acc: 0.4749
Epoch 612/1000
379/379 [==============================] - 0s 119us/step - loss: 1.7734 - acc: 0.4723
Epoch 613/1000
379/379 [==============================] - 0s 131us/step - loss: 1.7718 - acc: 0.4749
Epoch 614/1000
379/379 [==============================] - 0s 136us/step - loss: 1.7722 - acc: 0.4749
Epoch 615/1000
379/379 [==============================] - 0s 122us/step - loss: 1.7725 - acc: 0.4749
Epoch 616/1000
379/379 [==============================] - 0s 119us/step - loss: 1.7699 - acc: 0.4776
Epoch 617/1000
379/379 [==============================] - 0s 118us/step - loss: 1.7706 - acc: 0.4776
Epoch 618/1000
379/379 [==============================] - 0s 124us/step - loss: 1.7694 - acc: 0.4749
Epoch

379/379 [==============================] - 0s 114us/step - loss: 1.7356 - acc: 0.4855
Epoch 691/1000
379/379 [==============================] - 0s 113us/step - loss: 1.7328 - acc: 0.4908
Epoch 692/1000
379/379 [==============================] - 0s 130us/step - loss: 1.7325 - acc: 0.4881
Epoch 693/1000
379/379 [==============================] - 0s 121us/step - loss: 1.7323 - acc: 0.4855
Epoch 694/1000
379/379 [==============================] - 0s 112us/step - loss: 1.7316 - acc: 0.4855
Epoch 695/1000
379/379 [==============================] - 0s 116us/step - loss: 1.7316 - acc: 0.4855
Epoch 696/1000
379/379 [==============================] - 0s 122us/step - loss: 1.7315 - acc: 0.4828
Epoch 697/1000
379/379 [==============================] - 0s 112us/step - loss: 1.7301 - acc: 0.4855
Epoch 698/1000
379/379 [==============================] - 0s 119us/step - loss: 1.7298 - acc: 0.4855
Epoch 699/1000
379/379 [==============================] - 0s 115us/step - loss: 1.7288 - acc: 0.4881
Epoch

379/379 [==============================] - 0s 129us/step - loss: 1.6997 - acc: 0.4960
Epoch 772/1000
379/379 [==============================] - 0s 98us/step - loss: 1.6990 - acc: 0.4987
Epoch 773/1000
379/379 [==============================] - 0s 123us/step - loss: 1.6982 - acc: 0.5013
Epoch 774/1000
379/379 [==============================] - 0s 109us/step - loss: 1.6986 - acc: 0.4987
Epoch 775/1000
379/379 [==============================] - 0s 127us/step - loss: 1.6974 - acc: 0.4908
Epoch 776/1000
379/379 [==============================] - 0s 113us/step - loss: 1.6980 - acc: 0.5013
Epoch 777/1000
379/379 [==============================] - 0s 127us/step - loss: 1.6961 - acc: 0.4987
Epoch 778/1000
379/379 [==============================] - 0s 112us/step - loss: 1.6962 - acc: 0.4987
Epoch 779/1000
379/379 [==============================] - 0s 117us/step - loss: 1.6959 - acc: 0.4987
Epoch 780/1000
379/379 [==============================] - 0s 111us/step - loss: 1.6958 - acc: 0.4987
Epoch 

379/379 [==============================] - 0s 130us/step - loss: 1.6702 - acc: 0.5092
Epoch 853/1000
379/379 [==============================] - 0s 120us/step - loss: 1.6722 - acc: 0.5145
Epoch 854/1000
379/379 [==============================] - 0s 126us/step - loss: 1.6728 - acc: 0.5040
Epoch 855/1000
379/379 [==============================] - 0s 117us/step - loss: 1.6723 - acc: 0.5092
Epoch 856/1000
379/379 [==============================] - 0s 111us/step - loss: 1.6687 - acc: 0.5119
Epoch 857/1000
379/379 [==============================] - 0s 110us/step - loss: 1.6755 - acc: 0.4934
Epoch 858/1000
379/379 [==============================] - 0s 123us/step - loss: 1.6723 - acc: 0.5013
Epoch 859/1000
379/379 [==============================] - 0s 123us/step - loss: 1.6689 - acc: 0.4987
Epoch 860/1000
379/379 [==============================] - 0s 117us/step - loss: 1.6685 - acc: 0.5040
Epoch 861/1000
379/379 [==============================] - 0s 141us/step - loss: 1.6687 - acc: 0.5092
Epoch

379/379 [==============================] - 0s 126us/step - loss: 1.6451 - acc: 0.5092
Epoch 934/1000
379/379 [==============================] - 0s 116us/step - loss: 1.6447 - acc: 0.5119
Epoch 935/1000
379/379 [==============================] - 0s 122us/step - loss: 1.6445 - acc: 0.5119
Epoch 936/1000
379/379 [==============================] - 0s 124us/step - loss: 1.6443 - acc: 0.5145
Epoch 937/1000
379/379 [==============================] - 0s 116us/step - loss: 1.6441 - acc: 0.5092
Epoch 938/1000
379/379 [==============================] - 0s 128us/step - loss: 1.6451 - acc: 0.5040
Epoch 939/1000
379/379 [==============================] - 0s 123us/step - loss: 1.6442 - acc: 0.5066
Epoch 940/1000
379/379 [==============================] - 0s 121us/step - loss: 1.6436 - acc: 0.5092
Epoch 941/1000
379/379 [==============================] - 0s 116us/step - loss: 1.6420 - acc: 0.5092
Epoch 942/1000
379/379 [==============================] - 0s 108us/step - loss: 1.6416 - acc: 0.5092
Epoch

##### Bins reduced from 70 to 10

In [314]:
label_indices

{'S': 0,
 '1G1': 1,
 '1J0': 2,
 'E': 3,
 '3G0': 4,
 '1H0': 5,
 '1H1': 6,
 '3F0': 7,
 '3F1': 8,
 '3G1': 9,
 '4A0': 10,
 '1I0': 11,
 '2D0': 12,
 '2D1': 13,
 '1I1': 14,
 '1J1': 15,
 '4A1': 16,
 '2C1': 17,
 '2E0': 18,
 '2B1': 19,
 '2E1': 20,
 '3B0': 21,
 '3B1': 22,
 '3C0': 23,
 '3C1': 24,
 '3D0': 25,
 '3E0': 26,
 '3E1': 27,
 '1G0': 28,
 '3H0': 29}

In [315]:
path_df

new_col updated_path
0      1G0,2D1      1I0,2D1
1      3E0,1K0      3F0,1H0
2          1P0          1H0
3          3C0          3C0
4      3Z0,1K0      3F0,1H0
5         2AE1          2E1
6          2J1          2D1
7         3AL0          3C0
8          3C0          3C0
9         1AG0          1I0
10        1AF0          1H0
11         2T1          2D1
12        3AY0          3C0
13        3AD0          3B0
14   3BH0,2AS1      3F0,2E1
15   3AI0,2AS1      3F0,2E1
16        1AF0          1H0
17    2D1,1AG0      2D1,1I0
18   4AW0,2BQ1      4A0,2E1
19        1BF0          1H0
20    1AB0,1K0      1J0,1H0
21        3AD0          3B0
22        3AY0          3C0
23    3BX0,1V0      3E0,1H0
24        3BU0          3D0
25         3N0          3C0
26   1CF0,1AF0      1J0,1H0
27         3T0          3D0
28        3AD0          3B0
29   2BK1,1BI0      2D1,1J0
..         ...          ...
120       3AJ1          3G1
121       3DR1          3E1
122        1G1          1I1
123  3BZ1,1BL1      3B1,1J1
124       3BH1          3F1
125       1CX1          1I1
126   3S1,1AG1      3C1,1I1
127       3BM1          3E1
128       1AN1          1J1
129       1AB1          1J1
130        3Z1          3F1
131       3AI1          3F1
132    1V1,3U1      1H1,3G1
133       1BL1          1J1
134       1AF1          1H1
135       3CZ1          3G1
136       3CN1          3F1
137       3AI1          3F1
138       3CQ1          3E1
139       3AP1          3G1
140  1CX1,3AP1      1I1,3G1
141  1CP1,3CN1      1I1,3F1
142       1CX1          1I1
143        1K1          1H1
144  1CX1,3AI1      1I1,3F1
145       3AP1          3G1
146       3AJ1          3G1
147       1BI1          1J1
148   2S1,1CR1      2C1,1I1
149       3AI1          3F1

[150 rows x 2 columns]

In [321]:
combined_model_trial_4 = _create_combined_model()
label_model_trial_4 = _create_label_model()

def fit_model():

    y_cat = to_categorical(y)

    label_model_trial_4.compile(
        optimizer='adam', loss='categorical_crossentropy', metrics=['accuracy'])
    label_model_trial_4.fit(
        X, y_cat, batch_size=30, epochs=150, verbose=1, shuffle=True, validation_split=0.2)

    x_latent = get_hidden_x(path_latent_input, model=label_model_trial_4)

    combined_model_trial_4.compile(
        optimizer='adam', loss='categorical_crossentropy', metrics=['accuracy'])
    combined_model_trial_4.fit([x_latent, x_path], y_path,
                           batch_size=30, epochs=1000, verbose=1, shuffle=True)

In [322]:
fit_model()

Train on 120 samples, validate on 30 samples
Epoch 1/150
120/120 [==============================] - 1s 5ms/step - loss: 1.1326 - acc: 0.3583 - val_loss: 0.8648 - val_acc: 0.7000
Epoch 2/150
120/120 [==============================] - 0s 38us/step - loss: 0.9859 - acc: 0.4917 - val_loss: 0.9205 - val_acc: 0.6333
Epoch 3/150
120/120 [==============================] - 0s 40us/step - loss: 0.8784 - acc: 0.6833 - val_loss: 0.9834 - val_acc: 0.5667
Epoch 4/150
120/120 [==============================] - 0s 51us/step - loss: 0.7972 - acc: 0.7833 - val_loss: 1.0466 - val_acc: 0.4667
Epoch 5/150
120/120 [==============================] - 0s 50us/step - loss: 0.7326 - acc: 0.8083 - val_loss: 1.0968 - val_acc: 0.3667
Epoch 6/150
120/120 [==============================] - 0s 65us/step - loss: 0.6849 - acc: 0.8083 - val_loss: 1.1381 - val_acc: 0.3000
Epoch 7/150
120/120 [==============================] - 0s 65us/step - loss: 0.6451 - acc: 0.8167 - val_loss: 1.1530 - val_acc: 0.2333
Epoch 8/150
120/12

120/120 [==============================] - 0s 35us/step - loss: 0.2094 - acc: 0.9583 - val_loss: 0.6833 - val_acc: 0.7000
Epoch 62/150
120/120 [==============================] - 0s 42us/step - loss: 0.2051 - acc: 0.9750 - val_loss: 0.6711 - val_acc: 0.7333
Epoch 63/150
120/120 [==============================] - 0s 47us/step - loss: 0.2010 - acc: 0.9833 - val_loss: 0.6556 - val_acc: 0.7333
Epoch 64/150
120/120 [==============================] - 0s 39us/step - loss: 0.1971 - acc: 0.9833 - val_loss: 0.6442 - val_acc: 0.7333
Epoch 65/150
120/120 [==============================] - 0s 38us/step - loss: 0.1930 - acc: 0.9833 - val_loss: 0.6365 - val_acc: 0.7667
Epoch 66/150
120/120 [==============================] - 0s 35us/step - loss: 0.1894 - acc: 0.9833 - val_loss: 0.6238 - val_acc: 0.7667
Epoch 67/150
120/120 [==============================] - 0s 35us/step - loss: 0.1855 - acc: 0.9833 - val_loss: 0.6156 - val_acc: 0.7667
Epoch 68/150
120/120 [==============================] - 0s 36us/step

120/120 [==============================] - 0s 44us/step - loss: 0.0828 - acc: 0.9917 - val_loss: 0.3851 - val_acc: 0.8333
Epoch 122/150
120/120 [==============================] - 0s 44us/step - loss: 0.0817 - acc: 1.0000 - val_loss: 0.3819 - val_acc: 0.8333
Epoch 123/150
120/120 [==============================] - 0s 43us/step - loss: 0.0808 - acc: 0.9917 - val_loss: 0.3785 - val_acc: 0.8667
Epoch 124/150
120/120 [==============================] - 0s 76us/step - loss: 0.0799 - acc: 0.9917 - val_loss: 0.3728 - val_acc: 0.8667
Epoch 125/150
120/120 [==============================] - 0s 68us/step - loss: 0.0792 - acc: 0.9917 - val_loss: 0.3661 - val_acc: 0.8667
Epoch 126/150
120/120 [==============================] - 0s 62us/step - loss: 0.0785 - acc: 0.9917 - val_loss: 0.3743 - val_acc: 0.8667
Epoch 127/150
120/120 [==============================] - 0s 57us/step - loss: 0.0775 - acc: 0.9917 - val_loss: 0.3743 - val_acc: 0.8667
Epoch 128/150
120/120 [==============================] - 0s 70

379/379 [==============================] - 0s 129us/step - loss: 2.1198 - acc: 0.3958
Epoch 43/1000
379/379 [==============================] - 0s 144us/step - loss: 2.1076 - acc: 0.3958
Epoch 44/1000
379/379 [==============================] - 0s 112us/step - loss: 2.0958 - acc: 0.3958
Epoch 45/1000
379/379 [==============================] - 0s 110us/step - loss: 2.0839 - acc: 0.3958
Epoch 46/1000
379/379 [==============================] - 0s 130us/step - loss: 2.0725 - acc: 0.3958
Epoch 47/1000
379/379 [==============================] - 0s 137us/step - loss: 2.0615 - acc: 0.3958
Epoch 48/1000
379/379 [==============================] - 0s 127us/step - loss: 2.0504 - acc: 0.3958
Epoch 49/1000
379/379 [==============================] - 0s 118us/step - loss: 2.0402 - acc: 0.3958
Epoch 50/1000
379/379 [==============================] - 0s 122us/step - loss: 2.0303 - acc: 0.3984
Epoch 51/1000
379/379 [==============================] - 0s 128us/step - loss: 2.0205 - acc: 0.4116
Epoch 52/1000


379/379 [==============================] - 0s 103us/step - loss: 1.7329 - acc: 0.4723
Epoch 124/1000
379/379 [==============================] - 0s 107us/step - loss: 1.7312 - acc: 0.4697
Epoch 125/1000
379/379 [==============================] - 0s 127us/step - loss: 1.7297 - acc: 0.4723
Epoch 126/1000
379/379 [==============================] - 0s 111us/step - loss: 1.7286 - acc: 0.4723
Epoch 127/1000
379/379 [==============================] - 0s 127us/step - loss: 1.7258 - acc: 0.4697
Epoch 128/1000
379/379 [==============================] - 0s 120us/step - loss: 1.7256 - acc: 0.4723
Epoch 129/1000
379/379 [==============================] - 0s 114us/step - loss: 1.7269 - acc: 0.4723
Epoch 130/1000
379/379 [==============================] - 0s 113us/step - loss: 1.7236 - acc: 0.4723
Epoch 131/1000
379/379 [==============================] - 0s 114us/step - loss: 1.7213 - acc: 0.4697
Epoch 132/1000
379/379 [==============================] - 0s 130us/step - loss: 1.7201 - acc: 0.4697
Epoch

...

379/379 [==============================] - 0s 125us/step - loss: 1.2961 - acc: 0.5646
Epoch 610/1000
379/379 [==============================] - 0s 118us/step - loss: 1.2943 - acc: 0.5673
Epoch 611/1000
379/379 [==============================] - 0s 116us/step - loss: 1.2958 - acc: 0.5673
Epoch 612/1000
379/379 [==============================] - 0s 125us/step - loss: 1.2951 - acc: 0.5646
Epoch 613/1000
379/379 [==============================] - 0s 131us/step - loss: 1.2951 - acc: 0.5673
Epoch 614/1000
379/379 [==============================] - 0s 123us/step - loss: 1.2945 - acc: 0.5673
Epoch 615/1000
379/379 [==============================] - 0s 136us/step - loss: 1.2946 - acc: 0.5673
Epoch 616/1000
379/379 [==============================] - 0s 125us/step - loss: 1.2950 - acc: 0.5699
Epoch 617/1000
379/379 [==============================] - 0s 141us/step - loss: 1.2933 - acc: 0.5699
Epoch 618/1000
379/379 [==============================] - 0s 118us/step - loss: 1.2946 - acc: 0.5620
Epoch

379/379 [==============================] - 0s 159us/step - loss: 1.2750 - acc: 0.5726
Epoch 691/1000
379/379 [==============================] - 0s 139us/step - loss: 1.2751 - acc: 0.5726
Epoch 692/1000
379/379 [==============================] - 0s 140us/step - loss: 1.2745 - acc: 0.5726
Epoch 693/1000
379/379 [==============================] - 0s 134us/step - loss: 1.2741 - acc: 0.5752
Epoch 694/1000
379/379 [==============================] - 0s 141us/step - loss: 1.2743 - acc: 0.5752
Epoch 695/1000
379/379 [==============================] - 0s 140us/step - loss: 1.2750 - acc: 0.5726
Epoch 696/1000
379/379 [==============================] - 0s 131us/step - loss: 1.2761 - acc: 0.5726
Epoch 697/1000
379/379 [==============================] - 0s 134us/step - loss: 1.2731 - acc: 0.5752
Epoch 698/1000
379/379 [==============================] - 0s 144us/step - loss: 1.2728 - acc: 0.5752
Epoch 699/1000
379/379 [==============================] - 0s 149us/step - loss: 1.2729 - acc: 0.5726
Epoch

379/379 [==============================] - 0s 134us/step - loss: 1.2561 - acc: 0.5805
Epoch 772/1000
379/379 [==============================] - 0s 130us/step - loss: 1.2550 - acc: 0.5805
Epoch 773/1000
379/379 [==============================] - 0s 134us/step - loss: 1.2551 - acc: 0.5778
Epoch 774/1000
379/379 [==============================] - 0s 130us/step - loss: 1.2559 - acc: 0.5805
Epoch 775/1000
379/379 [==============================] - 0s 141us/step - loss: 1.2555 - acc: 0.5805
Epoch 776/1000
379/379 [==============================] - 0s 144us/step - loss: 1.2551 - acc: 0.5805
Epoch 777/1000
379/379 [==============================] - 0s 151us/step - loss: 1.2537 - acc: 0.5805
Epoch 778/1000
379/379 [==============================] - 0s 130us/step - loss: 1.2539 - acc: 0.5805
Epoch 779/1000
379/379 [==============================] - 0s 145us/step - loss: 1.2541 - acc: 0.5805
Epoch 780/1000
379/379 [==============================] - 0s 136us/step - loss: 1.2530 - acc: 0.5805
Epoch

379/379 [==============================] - 0s 132us/step - loss: 1.2378 - acc: 0.5831
Epoch 853/1000
379/379 [==============================] - 0s 129us/step - loss: 1.2388 - acc: 0.5831
Epoch 854/1000
379/379 [==============================] - 0s 138us/step - loss: 1.2392 - acc: 0.5805
Epoch 855/1000
379/379 [==============================] - 0s 128us/step - loss: 1.2396 - acc: 0.5778
Epoch 856/1000
379/379 [==============================] - 0s 136us/step - loss: 1.2386 - acc: 0.5805
Epoch 857/1000
379/379 [==============================] - 0s 138us/step - loss: 1.2370 - acc: 0.5805
Epoch 858/1000
379/379 [==============================] - 0s 146us/step - loss: 1.2378 - acc: 0.5778
Epoch 859/1000
379/379 [==============================] - 0s 126us/step - loss: 1.2402 - acc: 0.5805
Epoch 860/1000
379/379 [==============================] - 0s 145us/step - loss: 1.2370 - acc: 0.5778
Epoch 861/1000
379/379 [==============================] - 0s 151us/step - loss: 1.2367 - acc: 0.5805
Epoch

379/379 [==============================] - 0s 129us/step - loss: 1.2234 - acc: 0.5858
Epoch 934/1000
379/379 [==============================] - 0s 117us/step - loss: 1.2246 - acc: 0.5805
Epoch 935/1000
379/379 [==============================] - 0s 140us/step - loss: 1.2215 - acc: 0.5831
Epoch 936/1000
379/379 [==============================] - 0s 123us/step - loss: 1.2224 - acc: 0.5831
Epoch 937/1000
379/379 [==============================] - 0s 134us/step - loss: 1.2241 - acc: 0.5805
Epoch 938/1000
379/379 [==============================] - 0s 139us/step - loss: 1.2218 - acc: 0.5831
Epoch 939/1000
379/379 [==============================] - 0s 130us/step - loss: 1.2220 - acc: 0.5805
Epoch 940/1000
379/379 [==============================] - 0s 133us/step - loss: 1.2202 - acc: 0.5778
Epoch 941/1000
379/379 [==============================] - 0s 120us/step - loss: 1.2209 - acc: 0.5805
Epoch 942/1000
379/379 [==============================] - 0s 126us/step - loss: 1.2240 - acc: 0.5884
Epoch

In [317]:
x_path.shape

(379, 5, 30)

In [320]:
y_path.shape

(379, 30)

In [323]:
combined_model_trial_4.summary()

__________________________________________________________________________________________________
Layer (type)                    Output Shape         Param #     Connected to                     
label_ip (InputLayer)           (None, 5)            0                                            
__________________________________________________________________________________________________
dec_feat_ip (InputLayer)        (None, 5, 30)        0                                            
__________________________________________________________________________________________________
gru_seq (GRU)                   (None, 5)            540         dec_feat_ip[0][0]                
                                                                 label_ip[0][0]                   
__________________________________________________________________________________________________
cat (Concatenate)               (None, 10)           0           label_ip[0][0]                   
          

##### Bins reduced from 70 to 5

In [55]:
label_indices

{'S': 0,
 '1D0': 1,
 '2B1': 2,
 'E': 3,
 '1D1': 4,
 '1E0': 5,
 '1E1': 6,
 '3C0': 7,
 '3C1': 8,
 '3D0': 9,
 '3D1': 10,
 '4A0': 11,
 '4A1': 12,
 '2B0': 13,
 '2A1': 14,
 '2C0': 15,
 '3A0': 16,
 '3A1': 17,
 '3B0': 18,
 '3B1': 19,
 '1C0': 20,
 '1C1': 21,
 '2C1': 22}

In [57]:
path_df.head(15)

new_col updated_path
0     1G0,2D1      1E0,2B1
1     3E0,1K0      3C0,1D0
2         1P0          1D0
3         3C0          3A0
4     3Z0,1K0      3C0,1D0
5        2AE1          2B1
6         2J1          2B1
7        3AL0          3A0
8         3C0          3A0
9        1AG0          1E0
10       1AF0          1D0
11        2T1          2B1
12       3AY0          3B0
13       3AD0          3A0
14  3BH0,2AS1      3C0,2B1

In [354]:
path_df

new_col updated_path
0      1G0,2D1      1D0,2B1
1      3E0,1K0      3C0,1D0
2          1P0          1D0
3          3C0          3A0
4      3Z0,1K0      3C0,1D0
5         2AE1          2B1
6          2J1          2B1
7         3AL0          3A0
8          3C0          3A0
9         1AG0          1E0
10        1AF0          1D0
11         2T1          2B1
12        3AY0          3A0
13        3AD0          3A0
14   3BH0,2AS1      3C0,2B1
15   3AI0,2AS1      3C0,2B1
16        1AF0          1D0
17    2D1,1AG0      2B1,1E0
18   4AW0,2BQ1      4A0,2B1
19        1BF0          1D0
20    1AB0,1K0      1E0,1D0
21        3AD0          3A0
22        3AY0          3A0
23    3BX0,1V0      3C0,1D0
24        3BU0          3B0
25         3N0          3B0
26   1CF0,1AF0      1E0,1D0
27         3T0          3B0
28        3AD0          3A0
29   2BK1,1BI0      2B1,1E0
..         ...          ...
120       3AJ1          3C1
121       3DR1          3C1
122        1G1          1D1
123  3BZ1,1BL1      3A1,1E1
124       3BH1          3C1
125       1CX1          1D1
126   3S1,1AG1      3B1,1E1
127       3BM1          3C1
128       1AN1          1E1
129       1AB1          1E1
130        3Z1          3C1
131       3AI1          3C1
132    1V1,3U1      1D1,3C1
133       1BL1          1E1
134       1AF1          1D1
135       3CZ1          3C1
136       3CN1          3C1
137       3AI1          3C1
138       3CQ1          3C1
139       3AP1          3C1
140  1CX1,3AP1      1D1,3C1
141  1CP1,3CN1      1D1,3C1
142       1CX1          1D1
143        1K1          1D1
144  1CX1,3AI1      1D1,3C1
145       3AP1          3C1
146       3AJ1          3C1
147       1BI1          1E1
148   2S1,1CR1      2B1,1D1
149       3AI1          3C1

[150 rows x 2 columns]

In [58]:
path_latent_input.shape

(379, 4)

In [78]:
np.unique(path_df.loc[:,'updated_path'], return_counts=True)

(array(['1D0', '1D0,2B1', '1D1', '1D1,1E0', '1D1,1E1', '1D1,3C0',
        '1D1,3C1', '1D1,3D0', '1D1,3D1', '1D1,4A0', '1D1,4A1', '1E0',
        '1E0,1D0', '1E0,1D1', '1E0,2B0', '1E0,2B1', '1E1', '1E1,3C1',
        '1E1,3D0', '2B0,1E0', '2B0,1E1', '2B0,2A1,1E1', '2B0,3C0',
        '2B0,4A0', '2B1', '2B1,1D1', '2B1,1E0', '2C0,3C0', '3A0',
        '3A1,1E0', '3A1,1E1', '3A1,2B0', '3A1,3C0', '3A1,3C1', '3A1,3D0',
        '3B0', '3B1,1E0', '3B1,1E1', '3B1,3D0', '3B1,4A0', '3C0',
        '3C0,1C0', '3C0,1C1', '3C0,1D0', '3C0,1D1', '3C0,1E1', '3C0,2B0',
        '3C0,2B1', '3C1', '3D0', '3D0,1D0', '3D0,1D1', '3D0,2B0', '3D1',
        '4A0,1D1', '4A0,2C1', '4A1'], dtype=object),
 array([11,  1,  5,  4,  1,  3,  3,  1,  2,  1,  1,  2,  2,  2,  1,  1,  8,
         2,  1,  4,  1,  1,  1,  1,  4,  1,  2,  2, 10,  3,  1,  1,  3,  1,
         1,  6,  1,  1,  1,  1,  1,  1,  1,  4,  7,  1,  3,  3, 18,  2,  1,
         1,  1,  2,  1,  1,  3]))

In [71]:
combined_model_trial_5 = _create_combined_model()
label_model_trial_5 = _create_label_model()

def fit_model():

    y_cat = to_categorical(y)

    label_model_trial_5.compile(
        optimizer='adam', loss='categorical_crossentropy', metrics=['accuracy'])
    label_model_trial_5.fit(
        X, y_cat, batch_size=30, epochs=150, verbose=1, shuffle=True, validation_split=0.2)

    x_latent = get_hidden_x(path_latent_input, model=label_model_trial_5)

    combined_model_trial_5.compile(
        optimizer='adam', loss='categorical_crossentropy', metrics=['accuracy'])
    combined_model_trial_5.fit([x_latent, x_path], y_path,
                           batch_size=30, epochs=400, verbose=1)

In [63]:
x_path.shape

(379, 5, 23)

In [64]:
y_path.shape

(379, 23)

In [72]:
fit_model()

Train on 120 samples, validate on 30 samples
Epoch 1/150
120/120 [==============================] - 0s 4ms/step - loss: 1.0632 - acc: 0.4750 - val_loss: 1.1369 - val_acc: 0.0000e+00
Epoch 2/150
120/120 [==============================] - 0s 62us/step - loss: 0.9239 - acc: 0.6000 - val_loss: 1.1298 - val_acc: 0.0333
Epoch 3/150
120/120 [==============================] - 0s 53us/step - loss: 0.8170 - acc: 0.6250 - val_loss: 1.1319 - val_acc: 0.0000e+00
Epoch 4/150
120/120 [==============================] - 0s 56us/step - loss: 0.7304 - acc: 0.7250 - val_loss: 1.1406 - val_acc: 0.0000e+00
Epoch 5/150
120/120 [==============================] - 0s 76us/step - loss: 0.6642 - acc: 0.7667 - val_loss: 1.1509 - val_acc: 0.0000e+00
Epoch 6/150
120/120 [==============================] - 0s 44us/step - loss: 0.6153 - acc: 0.8083 - val_loss: 1.1626 - val_acc: 0.0000e+00
Epoch 7/150
120/120 [==============================] - 0s 77us/step - loss: 0.5762 - acc: 0.8167 - val_loss: 1.1716 - val_acc: 0.000

120/120 [==============================] - 0s 86us/step - loss: 0.2893 - acc: 0.8417 - val_loss: 0.9351 - val_acc: 0.0333
Epoch 61/150
120/120 [==============================] - 0s 51us/step - loss: 0.2867 - acc: 0.8417 - val_loss: 0.9295 - val_acc: 0.0333
Epoch 62/150
120/120 [==============================] - 0s 33us/step - loss: 0.2838 - acc: 0.8417 - val_loss: 0.9242 - val_acc: 0.0333
Epoch 63/150
120/120 [==============================] - 0s 36us/step - loss: 0.2812 - acc: 0.8417 - val_loss: 0.9186 - val_acc: 0.0333
Epoch 64/150
120/120 [==============================] - 0s 67us/step - loss: 0.2784 - acc: 0.8417 - val_loss: 0.9043 - val_acc: 0.0333
Epoch 65/150
120/120 [==============================] - 0s 45us/step - loss: 0.2754 - acc: 0.8500 - val_loss: 0.8983 - val_acc: 0.0333
Epoch 66/150
120/120 [==============================] - 0s 48us/step - loss: 0.2727 - acc: 0.8500 - val_loss: 0.8864 - val_acc: 0.0333
Epoch 67/150
120/120 [==============================] - 0s 41us/step

120/120 [==============================] - 0s 44us/step - loss: 0.1293 - acc: 1.0000 - val_loss: 0.4952 - val_acc: 0.8000
Epoch 121/150
120/120 [==============================] - 0s 52us/step - loss: 0.1276 - acc: 0.9917 - val_loss: 0.5014 - val_acc: 0.8000
Epoch 122/150
120/120 [==============================] - 0s 41us/step - loss: 0.1258 - acc: 1.0000 - val_loss: 0.4995 - val_acc: 0.8000
Epoch 123/150
120/120 [==============================] - 0s 40us/step - loss: 0.1240 - acc: 1.0000 - val_loss: 0.4863 - val_acc: 0.8000
Epoch 124/150
120/120 [==============================] - 0s 44us/step - loss: 0.1223 - acc: 1.0000 - val_loss: 0.4750 - val_acc: 0.8000
Epoch 125/150
120/120 [==============================] - 0s 49us/step - loss: 0.1204 - acc: 1.0000 - val_loss: 0.4738 - val_acc: 0.8000
Epoch 126/150
120/120 [==============================] - 0s 37us/step - loss: 0.1188 - acc: 1.0000 - val_loss: 0.4767 - val_acc: 0.8000
Epoch 127/150
120/120 [==============================] - 0s 49

379/379 [==============================] - 0s 126us/step - loss: 1.9012 - acc: 0.3958
Epoch 42/400
379/379 [==============================] - 0s 99us/step - loss: 1.8917 - acc: 0.3958
Epoch 43/400
379/379 [==============================] - 0s 110us/step - loss: 1.8825 - acc: 0.3958
Epoch 44/400
379/379 [==============================] - 0s 109us/step - loss: 1.8720 - acc: 0.4063
Epoch 45/400
379/379 [==============================] - 0s 120us/step - loss: 1.8615 - acc: 0.4116
Epoch 46/400
379/379 [==============================] - 0s 127us/step - loss: 1.8511 - acc: 0.4169
Epoch 47/400
379/379 [==============================] - 0s 116us/step - loss: 1.8398 - acc: 0.4169
Epoch 48/400
379/379 [==============================] - 0s 112us/step - loss: 1.8282 - acc: 0.4169
Epoch 49/400
379/379 [==============================] - 0s 106us/step - loss: 1.8163 - acc: 0.4090
Epoch 50/400
379/379 [==============================] - 0s 126us/step - loss: 1.8034 - acc: 0.4063
Epoch 51/400
379/379 [==

379/379 [==============================] - 0s 131us/step - loss: 1.3163 - acc: 0.5620
Epoch 124/400
379/379 [==============================] - 0s 131us/step - loss: 1.3132 - acc: 0.5646
Epoch 125/400
379/379 [==============================] - 0s 129us/step - loss: 1.3128 - acc: 0.5673
Epoch 126/400
379/379 [==============================] - 0s 119us/step - loss: 1.3087 - acc: 0.5673
Epoch 127/400
379/379 [==============================] - 0s 116us/step - loss: 1.3073 - acc: 0.5620
Epoch 128/400
379/379 [==============================] - 0s 109us/step - loss: 1.3049 - acc: 0.5646
Epoch 129/400
379/379 [==============================] - 0s 116us/step - loss: 1.3020 - acc: 0.5646
Epoch 130/400
379/379 [==============================] - 0s 96us/step - loss: 1.3008 - acc: 0.5646
Epoch 131/400
379/379 [==============================] - 0s 112us/step - loss: 1.2993 - acc: 0.5646
Epoch 132/400
379/379 [==============================] - 0s 111us/step - loss: 1.2983 - acc: 0.5646
Epoch 133/400
3

379/379 [==============================] - 0s 133us/step - loss: 1.1918 - acc: 0.5831
Epoch 206/400
379/379 [==============================] - 0s 125us/step - loss: 1.1904 - acc: 0.5805
Epoch 207/400
379/379 [==============================] - 0s 100us/step - loss: 1.1891 - acc: 0.5805
Epoch 208/400
379/379 [==============================] - 0s 127us/step - loss: 1.1875 - acc: 0.5831
Epoch 209/400
379/379 [==============================] - 0s 122us/step - loss: 1.1868 - acc: 0.5831
Epoch 210/400
379/379 [==============================] - 0s 101us/step - loss: 1.1868 - acc: 0.5831
Epoch 211/400
379/379 [==============================] - 0s 119us/step - loss: 1.1854 - acc: 0.5831
Epoch 212/400
379/379 [==============================] - 0s 107us/step - loss: 1.1841 - acc: 0.5858
Epoch 213/400
379/379 [==============================] - 0s 106us/step - loss: 1.1837 - acc: 0.5831
Epoch 214/400
379/379 [==============================] - 0s 101us/step - loss: 1.1846 - acc: 0.5778
Epoch 215/400


379/379 [==============================] - 0s 105us/step - loss: 1.1398 - acc: 0.5858
Epoch 288/400
379/379 [==============================] - 0s 109us/step - loss: 1.1362 - acc: 0.5910
Epoch 289/400
379/379 [==============================] - 0s 104us/step - loss: 1.1383 - acc: 0.5963
Epoch 290/400
379/379 [==============================] - 0s 95us/step - loss: 1.1362 - acc: 0.5937
Epoch 291/400
379/379 [==============================] - 0s 99us/step - loss: 1.1354 - acc: 0.5884
Epoch 292/400
379/379 [==============================] - 0s 114us/step - loss: 1.1364 - acc: 0.5884
Epoch 293/400
379/379 [==============================] - 0s 99us/step - loss: 1.1356 - acc: 0.5910
Epoch 294/400
379/379 [==============================] - 0s 99us/step - loss: 1.1355 - acc: 0.5910
Epoch 295/400
379/379 [==============================] - 0s 118us/step - loss: 1.1343 - acc: 0.5937
Epoch 296/400
379/379 [==============================] - 0s 114us/step - loss: 1.1353 - acc: 0.5910
Epoch 297/400
379/

379/379 [==============================] - 0s 99us/step - loss: 1.1137 - acc: 0.5963
Epoch 370/400
379/379 [==============================] - 0s 106us/step - loss: 1.1140 - acc: 0.5937
Epoch 371/400
379/379 [==============================] - 0s 103us/step - loss: 1.1133 - acc: 0.5937
Epoch 372/400
379/379 [==============================] - 0s 102us/step - loss: 1.1142 - acc: 0.5937
Epoch 373/400
379/379 [==============================] - 0s 108us/step - loss: 1.1152 - acc: 0.5910
Epoch 374/400
379/379 [==============================] - 0s 98us/step - loss: 1.1133 - acc: 0.5937
Epoch 375/400
379/379 [==============================] - 0s 101us/step - loss: 1.1147 - acc: 0.5910
Epoch 376/400
379/379 [==============================] - 0s 101us/step - loss: 1.1127 - acc: 0.5910
Epoch 377/400
379/379 [==============================] - 0s 95us/step - loss: 1.1142 - acc: 0.5937
Epoch 378/400
379/379 [==============================] - 0s 100us/step - loss: 1.1125 - acc: 0.5910
Epoch 379/400
379

In [68]:
combined_model_trial_5.summary()

__________________________________________________________________________________________________
Layer (type)                    Output Shape         Param #     Connected to                     
label_ip (InputLayer)           (None, 5)            0                                            
__________________________________________________________________________________________________
dec_feat_ip (InputLayer)        (None, 5, 23)        0                                            
__________________________________________________________________________________________________
gru_seq (GRU)                   (None, 5)            435         dec_feat_ip[0][0]                
                                                                 label_ip[0][0]                   
__________________________________________________________________________________________________
cat (Concatenate)               (None, 10)           0           label_ip[0][0]                   
          

In [ ]:
## Merging bins
# 1) Extract frequency
# 2) Reduce using EMD
# 3) Map to reduced bins using EMD flow
# 4) Update 'paths' using 'bin_labels'
# 5) Train RNN

In [365]:
test_dict = {20:{
    126: 0.81,
    124: 0.91,
    121: 0.43
}}

In [377]:
import operator

max(test_dict[20].items(), key=operator.itemgetter(1))[0]

126

In [360]:
test_dict.update({20:{127:0.45}})

In [361]:
test_dict

{20: {127: 0.45}}

In [363]:
test_dict.pop(20)

{127: 0.45}

In [376]:
from dict_deep import deep_get, deep_set, deep_del
deep_set(test_dict, [20, 126], 0.99)

1

In [374]:
test_dict

{20: {126: 0.45, 124: 0.91, 121: 0.43, 127: 0.45}}